In [83]:
import numpy as np
import os
import pandas as pd
import arcpy

# Import the required ArcGIS API for Python modules
import arcgis
from arcgis.gis import GIS
gis = arcgis.GIS()
from arcgis.geoanalytics import manage_data

from IPython.display import display, Markdown

In [84]:
dirWork         = os.getcwd()
year            = '2018'
dirInput        = os.path.join(dirWork, r'data\data' + year                    )
dirIntermediate = os.path.join(dirWork, r'intermediate\intermediate' + year    )
dirResults      = os.path.join(dirWork, r'results\results' + year              )

print("Working Directory: "      + dirWork        )
print("Input Directory: "        + dirInput       )
print("Intermediate Directory: " + dirIntermediate)
print("Results Directory: "      + dirResults     )

Working Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns
Input Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\data\data2018
Intermediate Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\intermediate\intermediate2018
Results Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2018


In [85]:
dirIntermediate

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\intermediate\\intermediate2018'

In [86]:
#input filenames
fname_CityTownship_csv        = os.path.join(dirInput, 'citytownship.csv'                                         )
fname_CityTownship_shp        = os.path.join(dirInput, 'Municipalities_Township' + r'\Municipalities_Township.shp') 
fname_LEHDCommutePatterns_csv = os.path.join(dirInput, 'lehd_at_blockgroup_level' + year + '.csv'                 )
fname_UofUManualAllocation_csv= os.path.join(dirInput, '490351108004_Manual_Allocation.csv'                       )
fname_BlockGroups_shp         = os.path.join(dirInput, 'tl_2020_49_bg' + r'\tl_2020_49_sd_bg.shp'                    )
fname_Counties_AGRC_shp       = os.path.join(dirInput, 'Utah_County_Boundaries-shp' + r'\Counties.shp'            )
fname_LEHDCommutePatterns_csv

#intermediate
fname_CityTownshipCounty_BlockGroups_shp = os.path.join(dirIntermediate, 'citytownshipcounty_blockgroup_intersect.shp')
fname_CityTownshipWCodes_shp             = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes.shp')
fname_CountyWCodes_shp                   = os.path.join(dirIntermediate, 'Counties_withCodes.shp')
fname_CityTownshipWCodesUnionCounty_shp  = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes_Counties.shp')
fname_CityTownshipCountyWCodes_shp       = os.path.join(dirIntermediate, 'Municipalities_Townships_Counties_withCodes.shp')

#display(dirIntermediate)

#results geodatabase

fname_CityTownshipJSON = os.path.join(dirResults, "citytownshipdata.json")

gdb_LEHDCommutePatterns = "LEHDCommutePatterns.gdb"
fname_LEHDCommutePatterns_gdb = os.path.join(dirResults, gdb_LEHDCommutePatterns)

fname_CityTownshipWCodes = os.path.join(fname_LEHDCommutePatterns_gdb, 'Municipalities_Townships')
#fname_CityTownshipCounty = os.path.join(fname_LEHDCommutePatterns_gdb, 'Municipalities_Townships_Counties')

fname_BlockGroupsWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'BlockGroup_CommutePatterns_Number')
fname_BlockGroupsWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'BlockGroup_CommutePatterns_Percent_SelectedArea')
fname_BlockGroupsWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'BlockGroup_CommutePatterns_Percent_MapUnit')

fname_TractsWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'Tract_CommutePatterns_Number')
fname_TractsWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'Tract_CommutePatterns_Percent_SelectedArea')
fname_TractsWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'Tract_CommutePatterns_Percent_MapUnit')

fname_SDWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'SD_CommutePatterns_Number')
fname_SDWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'SD_CommutePatterns_Percent_SelectedArea')
fname_SDWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'SD_CommutePatterns_Percent_MapUnit')

fname_CitiesWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'City_CommutePatterns_Number')
fname_CitiesWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'City_CommutePatterns_Percent_SelectedArea')
fname_CitiesWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'City_CommutePatterns_Percent_MapUnit')

fname_Counties = os.path.join(fname_LEHDCommutePatterns_gdb, 'Counties')

def deleteIfExists(obj):
    if arcpy.Exists(obj): arcpy.Delete_management(obj)

#if results geodatabase doesn't exist, create it
print("Checking if " + fname_LEHDCommutePatterns_gdb + " exists...")
if not arcpy.Exists(os.path.join(dirResults, gdb_LEHDCommutePatterns)):
    print("Creating " + fname_LEHDCommutePatterns_gdb + "...")
    arcpy.management.CreateFileGDB(dirResults, gdb_LEHDCommutePatterns)
else:
    print(gdb_LEHDCommutePatterns + " exists...")

#print(AnalysisAreasInput)

Checking if c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2018\LEHDCommutePatterns.gdb exists...
LEHDCommutePatterns.gdb exists...


# Create Cities/Townships Feature Class with 3-Digit Code and County FIPS

In [87]:
#read in city/township shapefile, SHORTDESC is common field between this and CODE3 dataset
sdf_CityTownship = pd.DataFrame.spatial.from_featureclass(fname_CityTownship_shp)
display(sdf_CityTownship)

FID COUNTYNBR                              NAME  COUNTYSEAT  \
0      0        03                            Newton           0   
1      1        12                            Eureka           0   
2      2        29                        Huntsville           0   
3      3        27                        Springdale           0   
4      4        23                       Grantsville           0   
..   ...       ...                               ...         ...   
253  253        18          COPPERTON METRO TOWNSHIP           0   
254  254        18             KEARNS METRO TOWNSHIP           0   
255  255        18              MAGNA METRO TOWNSHIP           0   
256  256        18  EMIGRATION CANYON METRO TOWNSHIP           0   
257  257        18         WHITE CITY METRO TOWNSHIP           0   

             SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  IMSCOLOR  \
0               NEWTON 2018-09-19  54550     3100.0        047         2   
1               EUREKA 2018-09-19  24080     3010.0        009         2   
2           HUNTSVILLE 2014-10-15  37060     3030.0        019         4   
3           SPRINGDALE 2014-10-15  71840     3100.0        023         2   
4          GRANTSVILLE 2020-06-05  31120     3010.0        023         2   
..                 ...        ...    ...        ...        ...       ...   
253          Copperton 2016-12-27  15720        0.0                    0   
254             Kearns 2016-12-27  40470        0.0                    0   
255              Magna 2018-11-14  47290        0.0                    0   
256  Emigration Canyon 2016-12-27  22875        0.0                    0   
257         White City 2016-12-27  84050        0.0                    0   

               MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0                              801         813  1430705   
1                              693         695  1437974   
2           Huntsville         602         638  1428949   
3           Springdale         569         609  1432867   
4                             9152       11568  1428338   
..                 ...         ...         ...      ...   
253          Copperton         822         835            
254             Kearns       35769       36330            
255              Magna       26513       26949            
256  Emigration Canyon        1568        1592            
257         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {1C320704-F3E4-4D4F-A542-F6FFE3C36900}    0.071275    0.000240   
1    {E1F6AAAD-E49E-4820-A270-D3E7C2131A80}    0.100706    0.000395   
2    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
3    {E6E76C45-D141-47DF-9C96-D3D46F15A2B9}    0.193621    0.001208   
4    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
..                                      ...         ...         ...   
253  {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
254  {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
255  {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
256  {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
257  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE  
0    {"rings": [[[-112.00138477499996, 41.855487523...  
1    {"rings": [[[-112.09987515199998, 39.957670251...  
2    {"rings": [[[-111.76117535999998, 41.253396941...  
3    {"rings": [[[-112.97934207899999, 37.197581387...  
4    {"rings": [[[-112.37537669199997, 40.593511564...  
..                                                 ...  
253  {"rings": [[[-112.09934129299995, 40.562296682...  
254  {"rings": [[[-111.98660579699998, 40.667567316...  
255  {"rings": [[[-112.10619664199999, 40.691640141...  
256  {"rings": [[[-111.74338063899995, 40.818777216...  
257  {"rings": [[[-111.86273107599999, 40.581548957...  

[258 rows x 18 columns]

In [88]:
#rename METRO TOWNSHIPs to match CODE3 dataset
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'SHORTDESC'] = "WHITE CITY METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'SHORTDESC'] = "EMIGRATION CANYON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'SHORTDESC'] = "COPPERTON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'SHORTDESC'] = "MAGNA METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'SHORTDESC'] = "KEARNS METRO TOWNSHIP"

#give townships a better name
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'NAME'] = "White City"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'NAME'] = "Emigration Canyon"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'NAME'] = "Copperton"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'NAME'] = "Magna"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'NAME'] = "Kearns"

In [89]:
#read in township codes data
df_CityTownshipCodes = pd.read_csv(fname_CityTownship_csv)

#consolidate Hideout
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (WASATCH)']
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (SUMMIT)']

# get wfrc city/townships only
wfrc_towns  = ["AFK","ALA","ALP","BDL","BGM","BNT","BRT","CDF","CEN","CHA","CHL","CLF","CLI","CMT","COA","CWH","DAN","DRA","EAG","ELK","EMT","FAR","FCS","FFD","FRR","FTH","GLA","GOS","GRL","HAR","HDT","HDT","HEB","HER","HGH","HNF","HOL","HOO","HVL","IND","INT","KAY","KMS","KMT","LAY","LEH","LIN","MAP","MID","MLC","MMT","MRG","MSL","MUR","MWY","NOG","NSL","OGD","OKL","ORM","PAY","PGR","PLN","PRK","PRY","PVO","PVW","ROY","RVD","RVT","SAN","SAQ","SAR","SFK","SJC","SLC","SLM","SOG","SPV","SSL","SUN","SWE","SYR","TAY","TOO","UIN","VIN","WAT","WBG","WDL","WEB","WHT","WHV","WIL","WJC","WPT","WVC","WXC"]
df_CityTownshipCodes = df_CityTownshipCodes[df_CityTownshipCodes['CODE3'].isin(wfrc_towns)].reset_index(drop=True)

df_CityTownshipCodes

SHORTDESC CODE3
0          AMERICAN FORK   AFK
1                   ALTA   ALA
2                 ALPINE   ALP
3      BLUFFDALE (SL CO)   BDL
4    BLUFFDALE (UTAH CO)   BDL
..                   ...   ...
96          WILLARD CITY   WIL
97      WEST JORDAN CITY   WJC
98            WEST POINT   WPT
99      WEST VALLEY CITY   WVC
100     WOODS CROSS CITY   WXC

[101 rows x 2 columns]

In [90]:
#join spatial data frame to data frame with codes using SHORTDESC field as key between two
sdf_CityTownshipWCodes = pd.DataFrame.merge(sdf_CityTownship, df_CityTownshipCodes, on='SHORTDESC')

#export to intermediate location so that it can be used in dissolve function later (to remove cities that span counties)
sdf_CityTownshipWCodes.spatial.to_featureclass(fname_CityTownshipWCodes_shp)

display(sdf_CityTownshipWCodes)

FID COUNTYNBR               NAME  COUNTYSEAT  \
0      2        29         Huntsville           0   
1      4        23        Grantsville           0   
2      5        18          Bluffdale           0   
3      7        18           Herriman           0   
4     13        18       Taylorsville           0   
..   ...       ...                ...         ...   
96   253        18          Copperton           0   
97   254        18             Kearns           0   
98   255        18              Magna           0   
99   256        18  Emigration Canyon           0   
100  257        18         White City           0   

                            SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  \
0                          HUNTSVILLE 2014-10-15  37060     3030.0        019   
1                         GRANTSVILLE 2020-06-05  31120     3010.0        023   
2                   BLUFFDALE (SL CO) 2018-11-15  06810     3020.0        019   
3                       HERRIMAN TOWN 2019-11-22  34970     3035.0        060   
4                   TAYLORSVILLE CITY 2014-09-15  75360     3105.0        142   
..                                ...        ...    ...        ...        ...   
96           COPPERTON METRO TOWNSHIP 2016-12-27  15720        0.0              
97              KEARNS METRO TOWNSHIP 2016-12-27  40470        0.0              
98               MAGNA METRO TOWNSHIP 2018-11-14  47290        0.0              
99   EMIGRATION CANYON METRO TOWNSHIP 2016-12-27  22875        0.0              
100         WHITE CITY METRO TOWNSHIP 2016-12-27  84050        0.0              

     IMSCOLOR            MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0           4         Huntsville         602         638  1428949   
1           2                           9152       11568  1428338   
2           4                           7693       14699  1425844   
3           1                          22018       44877  1428675   
4           4       Taylorsville       59989       60192  1433206   
..        ...                ...         ...         ...      ...   
96          0          Copperton         822         835            
97          0             Kearns       35769       36330            
98          0              Magna       26513       26949            
99          0  Emigration Canyon        1568        1592            
100         0         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
1    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
2    {E52CE320-1532-4A57-8DB9-DFA819FBB85B}    0.303290    0.002868   
3    {3E78F48D-80B9-44DA-AC9F-836A7B4F1B8E}    0.617524    0.005943   
4    {3ADD19D5-EF23-4257-8048-E355AE283BC6}    0.303444    0.002991   
..                                      ...         ...         ...   
96   {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
97   {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
98   {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
99   {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
100  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE CODE3  
0    {"rings": [[[-111.76117535999998, 41.253396941...   HVL  
1    {"rings": [[[-112.37537669199997, 40.593511564...   GRL  
2    {"rings": [[[-111.94473146099995, 40.497759794...   BDL  
3    {"rings": [[[-112.06032590299998, 40.481954434...   HER  
4    {"rings": [[[-111.92081851599994, 40.685958404...   TAY  
..                                                 ...   ...  
96   {"rings": [[[-112.09934129299995, 40.562296682...   CMT  
97   {"rings": [[[-111.98660579699998, 40.667567316...   KMT  
98   {"rings": [[[-112.10619664199999, 40.691640141...   MMT  
99   {"rings": [[[-111.74338063899995, 40.818777216...   EMT  
100  {"rings": [[[-1

In [91]:
#dissolve by code, due to some cities spanning counties and having multiple records in codes and/or munis/townships
deleteIfExists(fname_CityTownshipWCodes)
arcpy.management.Dissolve(fname_CityTownshipWCodes_shp, fname_CityTownshipWCodes, ['CODE3'], [['NAME','FIRST'], ['COUNTYNBR','FIRST']])

sdf_CityTownshipWCodes = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodes)
sdf_CityTownshipWCodes = sdf_CityTownshipWCodes.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_countynbr":"FIRST_COUNTYNBR"})

display(sdf_CityTownshipWCodes)

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  
0   {"rings": [[[-111.77435121873373, 40.353624868...  
1   {"rings": [[[-111.59946851855727, 40.577431980...  
2   {"rings": [[[-111.75455302160464, 40.479513910...  
3   {"rings": [[[-111.9704071902396, 40.5008379065...  
4   {"rings": [[[-112.01898409573937, 41.535781784...  
..                                                ...  
92  {"rings": [[[-112.02999503963935, 41.391465965...  
93  {"rings": [[[-112.00475852158849, 40.638664299...  
94  {"rings": [[[-112.10779328273378, 41.143687479...  
95  {"rings": [[[-111.9626132723846, 40.7260972067...  
96  {"rings": [[[-111.89260269236036, 40.866220107...  

[97 rows x 5 columns]

In [92]:
df_CityTownship_NameCode = sdf_CityTownshipWCodes[['FIRST_NAME','CODE3','FIRST_COUNTYNBR']].copy()
df_CityTownship_NameCode = df_CityTownship_NameCode.sort_values(by=['FIRST_NAME'])

df_CityTownship_NameCode.columns = ('NAME','CODE3','COUNTYNBR')

display(df_CityTownship_NameCode)

#df_CityTownship_NameCode.to_json(os.path.join(dirResults, "citytownshipdata.json"),orient='records')
#export after adding workers and residents columns from data

NAME CODE3 COUNTYNBR
2             Alpine   ALP        25
1               Alta   ALA        18
0      American Fork   AFK        25
3          Bluffdale   BDL        18
5          Bountiful   BNT        06
..               ...   ...       ...
95  West Valley City   WVC        18
90        White City   WHT        18
92           Willard   WIL        02
88    Woodland Hills   WDL        25
96       Woods Cross   WXC        06

[97 rows x 3 columns]

In [93]:
#explicit definition of county for cross-county cities
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'BDL')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'DRA')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'HDT')), 'COUNTYNBR'] = '26'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'PRK')), 'COUNTYNBR'] = '22'

#read in county dataset
sdf_CountiesAGRC = pd.DataFrame.spatial.from_featureclass(fname_Counties_AGRC_shp)
sdf_CountiesAGRC['FIPS'   ] = sdf_CountiesAGRC['FIPS'].astype(int)
sdf_CountiesAGRC['zCOFIPS'] = 'z' + sdf_CountiesAGRC['FIPS'].astype(str).str.zfill(2) #add 'z' instead of 0, so that columns names won't start with number, and so sorts at end
sdf_CountiesAGRC['CO_NAME'] = sdf_CountiesAGRC['NAME'].str.title() + ' County'
display(sdf_CountiesAGRC)

#join by COUNTYNBR to get CO_FIPS
df_CityTownship_NameCode_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode,sdf_CountiesAGRC,on='COUNTYNBR')
display(df_CityTownship_NameCode_wCOFIPS)


df_CityTownship_NameCode = df_CityTownship_NameCode_wCOFIPS[['NAME_x','CODE3','zCOFIPS']]
df_CityTownship_NameCode.columns = ('NAME','CODE3','zCOFIPS')

display(df_CityTownship_NameCode)

FID  OBJECTID COUNTYNBR     ENTITYNBR  ENTITYYR        NAME  FIPS  \
0     0         1        03  2.010031e+09    2010.0       CACHE     5   
1     1         2        07  2.010071e+09    2010.0    DUCHESNE    13   
2     2         3        06  2.010061e+09    2010.0       DAVIS    11   
3     3         4        14  2.010141e+09    2010.0     MILLARD    27   
4     4         5        26  2.010261e+09    2010.0     WASATCH    51   
5     5         6        02  2.010021e+09    2010.0   BOX ELDER     3   
6     6         7        29  2.010291e+09    2010.0       WEBER    57   
7     7         8        12  2.010121e+09    2010.0        JUAB    23   
8     8         9        20  2.010201e+09    2010.0     SANPETE    39   
9     9        10        27  2.010271e+09    2010.0  WASHINGTON    53   
10   10        11        10  2.010101e+09    2010.0       GRAND    19   
11   11        12        17  2.010171e+09    2010.0        RICH    33   
12   12        13        04  2.010041e+09    2010.0      CARBON     7   
13   13        14        05  2.010051e+09    2010.0     DAGGETT     9   
14   14        15        01  2.010011e+09    2010.0      BEAVER     1   
15   15        16        21  2.010211e+09    2010.0      SEVIER    41   
16   16        17        09  2.010091e+09    2010.0    GARFIELD    17   
17   17        18        23  2.010231e+09    2010.0      TOOELE    45   
18   18        19        22  2.010221e+09    2010.0      SUMMIT    43   
19   19        20        16  2.010161e+09    2010.0       PIUTE    31   
20   20        21        24  2.010241e+09    2010.0      UINTAH    47   
21   21        22        11  2.010111e+09    2010.0        IRON    21   
22   22        23        08  2.010081e+09    2010.0       EMERY    15   
23   23        24        28  2.010281e+09    2010.0       WAYNE    55   
24   24        25        19  2.006191e+09    2006.0    SAN JUAN    37   
25   25        26        15  2.010151e+09    2010.0      MORGAN    29   
26   26        27        13  2.010131e+09    2010.0        KANE    25   
27   27        28        18  2.010181e+09    2010.0   SALT LAKE    35   
28   28        29        25  2.010251e+09    2010.0        UTAH    49   

   STATEPLANE  POP_LASTCE  POP_CURRES                                GlobalID  \
0       North      112656      128289  {59BEE5FF-00D6-414A-8CD9-3B9CF5FA25FB}   
1     Central       18607       19938  {AAE112BD-8D24-46EE-98CD-6689B87A14D1}   
2       North      306479      355481  {66DDE457-AF53-4B6D-9A7D-25F29FCCF626}   
3     Central       12503       13188  {DE7E933D-7233-4FBE-8D0C-5E0826EF05D7}   
4     Central       23530       34091  {1BAA04F5-D976-4917-BBF2-BE9C0F868C55}   
5       North       49975       56046  {2F4FBEBE-32DB-4A2D-A6D1-277679BDF193}   
6       North      231236      260213  {7F2E8776-C886-4F23-9D40-B861B1FB5391}   
7     Central       10246       12017  {7A6D2476-AE18-48E8-820B-CE97B805879F}   
8     Central       27822       30939  {323210BE-8E14-49FE-96FE-1C571E744993}   
9       South      138115      177556  {A13328EF-DD99-45B8-897C-A9FE2418E7CA}   
10    Central        9225        9754  {6246AFC5-101A-4D5B-8355-1910ED7CF71D}   
11      North        2264        2483  {0362BF2D-2424-4C0C-AF74-7FC49DDAF467}   
12    Central       21403       20463  {F9F3A18C-023D-42E3-AB18-3168BA3C9446}   
13      North        1059         950  {A1C114E4-6F14-452C-8157-F199752416CE}   
14      South        6629        6710  {14543D4C-CB01-4B05-AB19-DA399ABFD0ED}   
15    Central       20802       21620  {C9ECC2C2-7282-4B4E-9B47-D53CBB880820}   
16      South        5172        5051  {579769A4-4616-4A9B-92F0-9CFB2AEFD176}   
17    Central       58218       72259  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}   
18      North       36324       42145  {EE2B9872-701C-470A-A300-1DB609C67F24}   
19      South        1556        1479  {E4A8F0F6-AE75-4DAA-AF72-298AC8274F7D}   
20    Central       32588       35734  {8FAEFFAA-95C1-404A-8862-3CCC91A0C412}   
21      South       46163      

NAME_x CODE3 COUNTYNBR  FID  OBJECTID     ENTITYNBR  ENTITYYR  \
0           Alpine   ALP        25   28        29  2.010251e+09    2010.0   
1    American Fork   AFK        25   28        29  2.010251e+09    2010.0   
2       Cedar Fort   CDF        25   28        29  2.010251e+09    2010.0   
3      Cedar Hills   CHL        25   28        29  2.010251e+09    2010.0   
4   Eagle Mountain   EAG        25   28        29  2.010251e+09    2010.0   
..             ...   ...       ...  ...       ...           ...       ...   
92      West Haven   WHV        29    6         7  2.010291e+09    2010.0   
93     Grantsville   GRL        23   17        18  2.010231e+09    2010.0   
94          Tooele   TOO        23   17        18  2.010231e+09    2010.0   
95          Morgan   MRG        15   25        26  2.010151e+09    2010.0   
96       Santaquin   SAQ        12    7         8  2.010121e+09    2010.0   

    NAME_y  FIPS STATEPLANE  POP_LASTCE  POP_CURRES  \
0     UTAH    49    Central      516564      636235   
1     UTAH    49    Central      516564      636235   
2     UTAH    49    Central      516564      636235   
3     UTAH    49    Central      516564      636235   
4     UTAH    49    Central      516564      636235   
..     ...   ...        ...         ...         ...   
92   WEBER    57      North      231236      260213   
93  TOOELE    45    Central       58218       72259   
94  TOOELE    45    Central       58218       72259   
95  MORGAN    29      North        9469       12124   
96    JUAB    23    Central       10246       12017   

                                  GlobalID FIPS_STR  COLOR4  SHAPE_Leng  \
0   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
1   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
2   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
3   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
4   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
..                                     ...      ...     ...         ...   
92  {7F2E8776-C886-4F23-9D40-B861B1FB5391}    49057       1    2.973528   
93  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
94  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
95  {08CCA506-439E-4F9E-8302-50A6B9468EF5}    49029       2    2.862360   
96  {7A6D2476-AE18-48E8-820B-CE97B805879F}    49023       4    6.802360   

    SHAPE_Area                                              SHAPE zCOFIPS  \
0     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
1     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
2     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
3     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
4     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
..         ...                                                ...     ...   
92    0.183659  {'rings': [[[-111.92092166399999, 41.138676415...     z57   
93    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
94    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
95    0.169567  {'rings': [[[-111.51438719299995, 40.803633660...     z29   
96    0.926379  {'rings': [[[-112.17814760399995, 40.011304953...     z23   

          CO_NAME  
0     Utah County  
1     Utah County  
2     Utah County  
3     Utah County  
4     Utah County  
..            ...  
92   Weber County  
93  Tooele County  
94  Tooele County  
95  Morgan County  
96    Juab County  

[97 rows x 20 columns]

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

# Add Rows for County Level Totals

In [94]:
#read in csv with commute pattern data
df_LEHDCommutePatterns = pd.read_csv(fname_LEHDCommutePatterns_csv)

In [95]:
#get all column codes for summing
dfColCodes = df_LEHDCommutePatterns.loc[1:1,'AFK_h':'TTL_w'].T #get all columns from AFK_x through TTL_y
dfColCodes = dfColCodes.reset_index()

#convert to list for ease of calcs in future steps
dColCodes = dfColCodes['index'].values.tolist()
dColCodes

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


In [96]:
#normalize (melt) commute data so that columns become rows
df_LEHDCommutePatterns_Normalized = pd.melt(df_LEHDCommutePatterns, id_vars=['fakeid','GEOID'], value_vars=dColCodes)

#populate new fields with data from previous column names (ABC_x/y): CODE3 and Category (_x/_y)
df_LEHDCommutePatterns_Normalized['CODE3'   ] = df_LEHDCommutePatterns_Normalized['variable'].str[0:3]
df_LEHDCommutePatterns_Normalized['CATEGORY'] = df_LEHDCommutePatterns_Normalized['variable'].str[3:5]

#join with City/Township data using CODE3
df_LEHDCommutePatterns_Normalized_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode, df_LEHDCommutePatterns_Normalized, on='CODE3')
display(df_LEHDCommutePatterns_Normalized_wCOFIPS)

#get county totals for each GEOID by aggregating (groupby)
df_LEHDCommutePatterns_CountyTotals_Normalized = df_LEHDCommutePatterns_Normalized_wCOFIPS.groupby(['zCOFIPS','GEOID','CATEGORY'],as_index=False).agg({'value':np.sum})

#create column names for county level totals
df_LEHDCommutePatterns_CountyTotals_Normalized['zCOFIPS_wCat'] = df_LEHDCommutePatterns_CountyTotals_Normalized['zCOFIPS'] + df_LEHDCommutePatterns_CountyTotals_Normalized['CATEGORY']

#create pivot table to reverse normalization, returning structure to original format, but this time with county columns
df_LEHDCommutePatterns_CountyTotals = df_LEHDCommutePatterns_CountyTotals_Normalized.pivot(index='GEOID', columns='zCOFIPS_wCat')['value']

display(df_LEHDCommutePatterns_CountyTotals)

NAME CODE3 zCOFIPS  fakeid         GEOID variable  value CATEGORY
0          Alpine   ALP     z49       0        colSUM    ALP_h   4439       _h
1          Alpine   ALP     z49       0  490011001001    ALP_h      0       _h
2          Alpine   ALP     z49       1  490011001002    ALP_h      0       _h
3          Alpine   ALP     z49       2  490011001003    ALP_h      0       _h
4          Alpine   ALP     z49       3  490011002001    ALP_h      0       _h
...           ...   ...     ...     ...           ...      ...    ...      ...
391875  Santaquin   SAQ     z23    2014  490572112021    SAQ_w      0       _w
391876  Santaquin   SAQ     z23    2015  490572112022    SAQ_w      0       _w
391877  Santaquin   SAQ     z23    2016  490572112023    SAQ_w      0       _w
391878  Santaquin   SAQ     z23    2017  490572112024    SAQ_w      0       _w
391879  Santaquin   SAQ     z23    2018  490572112025    SAQ_w      0       _w

[391880 rows x 8 columns]

zCOFIPS_wCat  z03_h  z03_w   z11_h   z11_w  z23_h  z23_w  z29_h  z29_w  \
GEOID                                                                    
490011001001      0      0       5       0      0      0      1      1   
490011001002      1      0       5       4      1      0      0      0   
490011001003      1      0      12      11      1      0      0      0   
490011002001      1      0       0       0      0      0      0      0   
490011002002      0      0       0       5      0      1      0      0   
...             ...    ...     ...     ...    ...    ...    ...    ...   
490572112022     15      8     202     268      0      0     12      7   
490572112023      4      4      45     108      0      0      2      2   
490572112024      5      4      22      81      0      0      0      0   
490572112025     17      0     282      55      1      0     14      1   
colSUM        13468  10066  144906  109139   5590   1068   1852   1254   

zCOFIPS_wCat   z35_h   z35_w  z43_h  z43_w  z45_h  z45_w   z49_h   z49_w  \
GEOID                                                                      
490011001001      20      20      0      0      0      0      13      10   
490011001002      11      53      0      3      0      0      12      20   
490011001003      59      62      0      1      3      0      18      13   
490011002001       9      20      0      1      2      1      12       5   
490011002002       1      27      0      1      0      0       3      23   
...              ...     ...    ...    ...    ...    ...     ...     ...   
490572112022      42     297      1      3      4      0      29      60   
490572112023       6     127      1      0      2      1       7      19   
490572112024       4     106      0      1      0      0       3      15   
490572112025      61      75      2      0     10      2      47      12   
colSUM        540214  683132   6918  13798  21883   9402  249752  233966   

zCOFIPS_wCat  z51_h  z51_w   z57_h   z57_w  
GEOID                                       
490011001001      0      1       5       3  
490011001002      0      0       3       7  
490011001003      2      1       5       3  
490011002001      0      2       0       1  
490011002002      0      0       0       3  
...             ...    ...     ...     ...  
490572112022      2      1     354     592  
490572112023      0      0      83     235  
490572112024      1      0      71     213  
490572112025      4      1     503     126  
colSUM        11737   7438  107909  100189  

[2020 rows x 20 columns]

In [97]:
#add county columns to original dataset
df_LEHDCommutePatternsWCounty = pd.DataFrame.merge(df_LEHDCommutePatterns, df_LEHDCommutePatterns_CountyTotals, on='GEOID')
df_LEHDCommutePatterns = df_LEHDCommutePatternsWCounty

df_LEHDCommutePatterns

fakeid         GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0          0        colSUM  12283    162   4439   6482   9819  19759     71   
1          0  490011001001      0      0      0      0      0      0      0   
2          1  490011001002      1      0      0      0      0      1      0   
3          2  490011001003      1      0      0      2      1      2      0   
4          3  490011002001      1      0      0      0      1      0      0   
...      ...           ...    ...    ...    ...    ...    ...    ...    ...   
2015    2014  490572112021      1      0      1      0      5      3      0   
2016    2015  490572112022      2      0      0      0     10     13      0   
2017    2016  490572112023      0      0      0      0      3      0      0   
2018    2017  490572112024      0      0      0      0      4      0      0   
2019    2018  490572112025      1      0      1      0     12     14      0   

      CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0       322   7303    252   4420  13201   9986    462    759  16463    543   
1         0      0      0      0      2      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         0      0      0      1      0      1      0      0      1      1   
4         0      0      0      1      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      1      0      0     12     10      0      0      1      0   
2016      0      0      0      1     20     20      0      0      1      0   
2017      0      0      0      0      2      8      0      0      0      0   
2018      0      2      0      1      2      2      0      0      1      0   
2019      0      8      0      0     36     25      0      2      2      0   

      DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0     22021  14490   1554    737   9204    443     79   3038   2167    805   
1         0      0      0      0      0      0      0      0      0      0   
2         0      0      0      0      1      0      0      0      0      0   
3         3      1      0      0      1      0      0      0      0      0   
4         2      1      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      0      0      0      2      0      0      4      0      0   
2016      1      3      0      0     15      0      0      5      0      0   
2017      1      0      0      0      6      0      0      1      1      0   
2018      0      0      0      0      1      0      0      1      1      0   
2019      2      3      1      0      4      0      0     13      5      1   

      GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0       484   5114   3029    338   8019  16868   7738    358  14254   3663   
1         0      0      0      0      0      1      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         0      0      0      0      1      1      1      0      2      0   
4         0      0      0      0      0      1      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      3      2      0      0      1      0      0      1     10   
2016      0      1      7      0      1      2      0      1      1      6   
2017      0      0      7      0      0      0      1      0      0      2   
2018      0      0      0      0      0      0      0      0      0      1   
2019      0      3     11      0      2      2      2      0      5     19   

      HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0       278    119     50  12693    945  18712  31664  28872   5063   4592   
1         0      0      0      0      0      1      1      0      0      1   
2         0 

In [98]:
#remove UofU displaced block group
#superceeded by manual reallocation prior to data input prep
#
display(df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID']=='490351108004'])

#
#df_LEHDCommutePatterns = df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID'] != '490351108004']

#display(df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID']=='490351108004'])

fakeid         GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
631     630  490351108004      0      0      2      1      2      5      0   

     CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
631      0      1      0      1      8      1      0      0     26      0   

     DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
631      6      3      1      0      1      0      0      0      0      0   

     GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
631      0      2      0      0      1      7      2      0     35      0   

     HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
631      0      1      0      3      0      7      5      8      2      1   

     MID_h  MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  \
631     18     46      3      0      0     24      1      1      2      8   

     OKL_h  ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  \
631      0     10      1      3      0      1      0      6      0      1   

     RVD_h  RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  \
631      1      7     35      0      3      4     13     61      1      3   

     SPV_h  SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  \
631      2     16      2      1      1     20      9      0      0      0   

     WBG_h  WDL_h  WEB_h  WHT_h  WHV_h  WIL_h  WJC_h  WPT_h  WVC_h  WXC_h  \
631      0      0      0      2      0      0     26      1     32      1   

     TTL_h  AFK_w  ALA_w  ALP_w  BDL_w  BGM_w  BNT_w  BRT_w  CDF_w  CEN_w  \
631    529      5      2      0      3      1      4      0      0      1   

     CHA_w  CHL_w  CLF_w  CLI_w  CMT_w  COA_w  CWH_w  DAN_w  DRA_w  EAG_w  \
631      0      0      1      2      0      0     21      0     33      1   

     ELK_w  EMT_w  FAR_w  FCS_w  FFD_w  FRR_w  FTH_w  GLA_w  GOS_w  GRL_w  \
631      0      1      4      0      1      0      0      0      0      0   

     HAR_w  HDT_w  HEB_w  HER_w  HGH_w  HNF_w  HOL_w  HOO_w  HVL_w  IND_w  \
631      0      0      1      4      0      0     38      0      0      0   

     INT_w  KAY_w  KMS_w  KMT_w  LAY_w  LEH_w  LIN_w  MAP_w  MID_w  MLC_w  \
631      0      1      0      5      7     18      3      0     18     53   

     MMT_w  MRG_w  MSL_w  MUR_w  MWY_w  NOG_w  NSL_w  OGD_w  OKL_w  ORM_w  \
631      1      1      0     53      1      0      6     10      0     10   

     PAY_w  PGR_w  PLN_w  PRK_w  PRY_w  PVO_w  PVW_w  ROY_w  RVD_w  RVT_w  \
631      0      1      0      8      0     10      0      0      0      4   

     SAN_w  SAQ_w  SAR_w  SFK_w  SJC_w  SLC_w  SLM_w  SOG_w  SPV_w  SSL_w  \
631     18      0      2      1     23    287      0      2      1     33   

     SUN_w  SWE_w  SYR_w  TAY_w  TOO_w  UIN_w  VIN_w  WAT_w  WBG_w  WDL_w  \
631      0      0      0     30      2      0      0      0      0      0   

     WEB_w  WHT_w  WHV_w  WIL_w  WJC_w  WPT_w  WVC_w  WXC_w  TTL_w  z03_h  \
631      2      1      0      0     21      0     51      2    843      2   

     z03_w  z11_h  z11_w  z23_h  z23_w  z29_h  z29_w  z35_h  z35_w  z43_h  \
631      1     32     30      0      0      0      1    385    700      1   

     z43_w  z45_h  z45_w  z49_h  z49_w  z51_h  z51_w  z57_h  z57_w  
631      8     11      2     50     53      3      2     14     12

# Quick JSON export with some summary stats

In [99]:
#use row with "colSUM" as GEOID as total
df_LEHDCommutePatterns_ColSum = df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID'] == 'colSUM']
df_LEHDCommutePatterns_ColSum

fakeid   GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  \
0       0  colSUM  12283    162   4439   6482   9819  19759     71    322   

   CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  \
0   7303    252   4420  13201   9986    462    759  16463    543  22021   

   EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  \
0  14490   1554    737   9204    443     79   3038   2167    805    484   

   GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  \
0   5114   3029    338   8019  16868   7738    358  14254   3663    278   

   IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  MID_h  \
0    119     50  12693    945  18712  31664  28872   5063   4592  16743   

   MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  OKL_h  \
0  29657  14422   1852    926  25017   2250   9082   8249  39586    566   

   ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  RVD_h  \
0  44362   9726  15899   3050   3847   2633  39581   4090  18679   4214   

   RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  SPV_h  \
0  23541  47586   5590  13715  19747  32162  88595   4101   7846  16558   

   SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  WBG_h  \
0  11575   2604   3068  12129  30535  16769    619     90   4503    166   

   WDL_h  WEB_h  WHT_h  WHV_h  WIL_h  WJC_h  WPT_h  WVC_h  WXC_h    TTL_h  \
0    832   3131   2967   5306   1016  58202   4689  62980   5059  1390165   

   AFK_w  ALA_w  ALP_w  BDL_w  BGM_w  BNT_w  BRT_w  CDF_w  CEN_w  CHA_w  \
0  22429   1475   2785   4403   8977  11439     60     52   5640    189   

   CHL_w  CLF_w  CLI_w  CMT_w  COA_w  CWH_w  DAN_w  DRA_w  EAG_w  ELK_w  \
0    845  16589   2518     76    607  20362    183  37678   2057    310   

   EMT_w  FAR_w  FCS_w  FFD_w  FRR_w  FTH_w  GLA_w  GOS_w  GRL_w  HAR_w  \
0    135   9149     60    101   3082    446    162     57   1686   1616   

   HDT_w  HEB_w  HER_w  HGH_w  HNF_w  HOL_w  HOO_w  HVL_w  IND_w  INT_w  \
0      7   5824   4452   3028     46  10117    674     74     13      0   

   KAY_w  KMS_w  KMT_w  LAY_w  LEH_w  LIN_w  MAP_w  MID_w  MLC_w  MMT_w  \
0   8034   1153   4298  26964  33202  12517   1921  18321  48572   3019   

   MRG_w  MSL_w  MUR_w  MWY_w  NOG_w  NSL_w  OGD_w  OKL_w  ORM_w  PAY_w  \
0   1254   1821  44412   1168   2792  14796  58127    252  47620   6246   

   PGR_w  PLN_w  PRK_w  PRY_w  PVO_w  PVW_w  ROY_w  RVD_w  RVT_w  SAN_w  \
0  10685    845  11680    906  58416   2013   7599   7759  10200  47939   

   SAQ_w  SAR_w  SFK_w  SJC_w   SLC_w  SLM_w  SOG_w  SPV_w  SSL_w  SUN_w  \
0   1068   3498  12722  29894  238330   1602   6794  12550  34040   1194   

   SWE_w  SYR_w  TAY_w  TOO_w  UIN_w  VIN_w  WAT_w  WBG_w  WDL_w  WEB_w  \
0    636   3763  20760   7716    260    975   3351     54    186   2169   

   WHT_w  WHV_w  WIL_w  WJC_w  WPT_w  WVC_w  WXC_w    TTL_w  z03_h  z03_w  \
0    386   3382    183  35776   1049  68427   4753  1411279  13468  10066   

    z11_h   z11_w  z23_h  z23_w  z29_h  z29_w   z35_h   z35_w  z43_h  z43_w  \
0  144906  109139   5590   1068   1852   1254  540214  683132   6918  13798   

   z45_h  z45_w   z49_h   z49_w  z51_h  z51_w   z57_h   z57_w  
0  21883   9402  249752  233966  11737   7438  107909  100189

In [100]:
#prepare area columns for json
df_people = df_LEHDCommutePatterns_ColSum.loc[:,'AFK_h':'z57_w'].T #transpose
df_people = df_people.reset_index()
df_people['CATEGORY'] = df_people['index'].str[3:5]
df_people['index']    = df_people['index'].str[:3]
df_people

index       0 CATEGORY
0     AFK   12283       _h
1     ALA     162       _h
2     ALP    4439       _h
3     BDL    6482       _h
4     BGM    9819       _h
..    ...     ...      ...
211   z49  233966       _w
212   z51   11737       _h
213   z51    7438       _w
214   z57  107909       _h
215   z57  100189       _w

[216 rows x 3 columns]

In [101]:
#prepare x columns
df_people_x = df_people[df_people['CATEGORY'] == '_h']
df_people_x.columns = ('CODE3','people_h','CATEGORY')

df_people_x['CODE3'] = df_people_x['CODE3'].str[:3]

df_people_x = df_people_x.drop_duplicates() #some duplicate columns in dataset
display(df_people_x)

#prepare y columns
df_people_y = df_people[df_people['CATEGORY'] == '_w']
df_people_y.columns = ('CODE3','people_w','CATEGORY')

df_people_y['CODE3'] = df_people_y['CODE3'].str[:3]

df_people_y = df_people_y.drop_duplicates() #some duplicate columns in dataset
display(df_people_y)

df_people_x = df_people_x.drop(['CATEGORY'], axis=1)
df_people_y = df_people_y.drop(['CATEGORY'], axis=1)

#combine city/township data with x and y
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_NameCode,df_people_x, on='CODE3', how='right')
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_People  ,df_people_y, on='CODE3', how='right')                                           


C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


CODE3  people_h CATEGORY
0     AFK     12283       _h
1     ALA       162       _h
2     ALP      4439       _h
3     BDL      6482       _h
4     BGM      9819       _h
..    ...       ...      ...
206   z43      6918       _h
208   z45     21883       _h
210   z49    249752       _h
212   z51     11737       _h
214   z57    107909       _h

[108 rows x 3 columns]

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


CODE3  people_w CATEGORY
98    AFK     22429       _w
99    ALA      1475       _w
100   ALP      2785       _w
101   BDL      4403       _w
102   BGM      8977       _w
..    ...       ...      ...
207   z43     13798       _w
209   z45      9402       _w
211   z49    233966       _w
213   z51      7438       _w
215   z57    100189       _w

[108 rows x 3 columns]

In [102]:
#define county dataframe
df_CoNames = sdf_CountiesAGRC[['zCOFIPS','CO_NAME']]

#prepare dataframe for export to JSON, combining city/township
df_CityTownship_Export = pd.DataFrame.merge(df_CityTownship_People, df_CoNames, left_on='CODE3', right_on='zCOFIPS', how='left')

#for any null values, replace with zero(0)
df_CityTownship_Export = df_CityTownship_Export.fillna(0)

#Get city/township name and county name into one field
df_CityTownship_Export.loc[df_CityTownship_Export.CO_NAME != 0, 'NAME'] = df_CityTownship_Export['CO_NAME']

#filter by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_h','people_w']]

#change TTL (total) row to Counties subhead for correct positioning in dropdown

#don't include total row
df_CityTownship_Export = df_CityTownship_Export[df_CityTownship_Export['CODE3'] != 'TTL']

#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'NAME' ] = '---COUNTIES---'
#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'CODE3'] = 'y000'

#create a first letter field for sorting, to preserve COUNTIES with (z..) at bottom of sort, so can't use name as first sort
#df_CityTownship_Export['firstletter'] = df_CityTownship_Export['CODE3'].str[0:1]
#df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['firstletter','NAME'])
df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['NAME'])

#filter again by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_h','people_w']]

#rename columns with 'label' and 'value' to work better in javascript dojo convention
df_CityTownship_Export.columns = ('label','value','people_h','people_w')

#let's see what we got!!
display(df_CityTownship_Export)
    
#export to JSON
df_CityTownship_Export.to_json(fname_CityTownshipJSON,orient='records')

label value  people_h  people_w
2             Alpine   ALP      4439      2785
1               Alta   ALA       162      1475
0      American Fork   AFK     12283     22429
3          Bluffdale   BDL      6482      4403
5          Bountiful   BNT     19759     11439
..               ...   ...       ...       ...
95  West Valley City   WVC     62980     68427
90        White City   WHT      2967       386
92           Willard   WIL      1016       183
88    Woodland Hills   WDL       832       186
96       Woods Cross   WXC      5059      4753

[107 rows x 4 columns]

# Update ColCodes with Counties for summing

In [103]:
#get all column codes for summing
dfColCodesWCounty = df_LEHDCommutePatterns.loc[1:1,'AFK_h':'z57_w'].T
dfColCodesWCounty = dfColCodesWCounty.reset_index()
dColCodesWCounty = dfColCodesWCounty['index'].values.tolist()
dColCodesWCounty

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


# Add Unincorporated County Areas to Cities/Townships

In [104]:
#filter county dataset with only what we want
sdf_CountiesWCodes = sdf_CountiesAGRC[['zCOFIPS','CO_NAME','SHAPE']]
sdf_CountiesWCodes.columns = ('CODE3','FIRST_NAME','SHAPE')
display(sdf_CountiesWCodes)

#export a couple county spatial dataframes
sdf_CountiesWCodes.spatial.to_featureclass(fname_CountyWCodes_shp) #as shapefile for future use
sdf_CountiesWCodes.spatial.to_featureclass(fname_Counties) #for gdb for use in web app

CODE3         FIRST_NAME                                              SHAPE
0    z05       Cache County  {"rings": [[[-112.15617197899996, 41.997725941...
1    z13    Duchesne County  {"rings": [[[-110.25173670299995, 40.832347463...
2    z11       Davis County  {"rings": [[[-111.92092166399999, 41.138676415...
3    z27     Millard County  {"rings": [[[-112.23854898599996, 39.553633436...
4    z51     Wasatch County  {"rings": [[[-111.39572506599995, 40.690187842...
5    z03   Box Elder County  {"rings": [[[-113.47488592699995, 41.993309448...
6    z57       Weber County  {"rings": [[[-111.92092166399999, 41.138676415...
7    z23        Juab County  {"rings": [[[-112.17814760399995, 40.011304953...
8    z39     Sanpete County  {"rings": [[[-111.60347983999998, 39.812889279...
9    z53  Washington County  {"rings": [[[-113.47458777999998, 37.607168207...
10   z19       Grand County  {"rings": [[[-109.05510868899995, 39.498702060...
11   z33        Rich County  {"rings": [[[-111.04672602399995, 42.001708362...
12   z07      Carbon County  {"rings": [[[-111.05121454599998, 39.814071497...
13   z09     Daggett County  {"rings": [[[-109.05002513499994, 40.999895250...
14   z01      Beaver County  {"rings": [[[-112.51540546399997, 38.572850827...
15   z41      Sevier County  {"rings": [[[-111.84900514399999, 39.044355246...
16   z17    Garfield County  {"rings": [[[-112.26560199199997, 38.149879660...
17   z45      Tooele County  {"rings": [[[-112.44788691599996, 41.017030151...
18   z43      Summit County  {"rings": [[[-109.99967939799996, 40.997456621...
19   z31       Piute County  {"rings": [[[-112.33023683099998, 38.510834361...
20   z47      Uintah County  {"rings": [[[-109.04897471299995, 40.662656164...
21   z21        Iron County  {"rings": [[[-113.36588561299999, 38.148691452...
22   z15       Emery County  {"rings": [[[-111.24394073999997, 39.703588004...
23   z55       Wayne County  {"rings": [[[-111.70753983999998, 38.510152783...
24   z37    San Juan County  {"rings": [[[-109.77115733799997, 36.998238968...
25   z29      Morgan County  {"rings": [[[-111.51438719299995, 40.803633660...
26   z25        Kane County  {"rings": [[[-111.84536734499994, 37.535799155...
27   z35   Salt Lake County  {"rings": [[[-111.96851544299994, 40.871938834...
28   z49        Utah County  {"rings": [[[-111.59404929699997, 40.577075300...

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\Counties'

In [105]:
deleteIfExists(fname_CityTownshipWCodesUnionCounty_shp)

print ("Unioning city/township with county...")

#intersection parcels with analysis area types
arcpy.analysis.Union([fname_CityTownshipWCodes,fname_CountyWCodes_shp], fname_CityTownshipWCodesUnionCounty_shp)

sdf_CityTownshipWCodesCounty = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodesUnionCounty_shp)
sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_coun":"FIRST_COUN", "first_na_1":"FIRST_NA_1", "code3_1":"CODE3_1"})
sdf_CityTownshipWCodesCounty

Unioning city/township with county...


FID  FID_Munici CODE3        FIRST_NAME FIRST_COUN  Shape_Leng  \
0      0          -1                                       0.000000   
1      1          -1                                       0.000000   
2      2          -1                                       0.000000   
3      3          -1                                       0.000000   
4      4          -1                                       0.000000   
..   ...         ...   ...               ...        ...         ...   
154  154          75   SLC    Salt Lake City         18    1.346029   
155  155          50   MMT             Magna         18    0.756349   
156  156          96   WVC  West Valley City         18    0.614523   
157  157          70   SAN             Sandy         18    1.239008   
158  158          91   WHT        White City         18    0.147366   

     Shape_Area  FID_Counti  Id CODE3_1        FIRST_NA_1  \
0      0.000000           0   0     z05      Cache County   
1      0.000000           1   0     z13   Duchesne County   
2      0.000000           2   0     z11      Davis County   
3      0.000000           3   0     z27    Millard County   
4      0.000000           4   0     z51    Wasatch County   
..          ...         ...  ..     ...               ...   
154    0.030613          27   0     z35  Salt Lake County   
155    0.010342          27   0     z35  Salt Lake County   
156    0.009884          27   0     z35  Salt Lake County   
157    0.006653          27   0     z35  Salt Lake County   
158    0.000241          27   0     z35  Salt Lake County   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 12 columns]

In [106]:
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'CODE3'     ] = sdf_CityTownshipWCodesCounty['CODE3_1'   ]
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'FIRST_NAME'] = sdf_CityTownshipWCodesCounty['FIRST_NA_1'] + ' Unincorporated'

sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty[['FID_Munici','CODE3','FIRST_NAME','SHAPE']]

sdf_CityTownshipWCodesCounty.spatial.to_featureclass(fname_CityTownshipCountyWCodes_shp)
sdf_CityTownshipWCodesCounty

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


FID_Munici CODE3                      FIRST_NAME  \
0            -1   z05     Cache County Unincorporated   
1            -1   z13  Duchesne County Unincorporated   
2            -1   z11     Davis County Unincorporated   
3            -1   z27   Millard County Unincorporated   
4            -1   z51   Wasatch County Unincorporated   
..          ...   ...                             ...   
154          75   SLC                  Salt Lake City   
155          50   MMT                           Magna   
156          96   WVC                West Valley City   
157          70   SAN                           Sandy   
158          91   WHT                      White City   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 4 columns]

# Calculate Percent

In [107]:
#read block group shapefile
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_LEHDCommutePatterns = pd.DataFrame.merge(sdf_BlockGroups, df_LEHDCommutePatterns, on='GEOID')
display(sdf_BlockGroups)

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2015  2015      49      057  200900     16.0        2  490572009002   
2016  2016      49      057  201200     15.0        1  490572012001   
2017  2017      49      057  201200     15.0        2  490572012002   
2018  2018      49      057  201301     16.0        2  490572013012   
2019  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2015  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2016  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2017  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2018  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2019  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2015  -111.9636889 -111.963689   41.224827   85.863927   
2016  -111.9783667 -111.978367   41.212187  185.752109   
2017  -111.9706612 -111.970661   41.212304  108.139051   
2018  -111.9635764 -111.963576   41.216371   80.555404   
2019  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  
0     {"rings": [[[429468.0213051503, 4496405.233871...  
1     {"rings": [[[430494.91099986027, 4495540.43917...  
2     {"rings": [[[425457.5579433697, 4507873.987348...  
3     {"rings": [[[425448.36375707807, 4507253.27157...  
4     {"rings": [[[425435.2029181655, 4506380.698648...  
...                                                 ...  
2015  {"rings": [[[418807.4658959587, 4564213.682993...  
2016  {"rings": [[[417490.98019006505, 4562356.17136...  
2017  {"rings": [[[418380.1807087121, 4562347.716705...  
2018  {"rings": [[[418871.13447070273, 4563020.29370...  
2019  {"rings": [[[419571.11778565514, 4563028.08038...  

[2020 rows x 18 columns]

In [108]:
pd.set_option('display.max_columns', None)
df_LEHDCommutePatterns.loc[1:,'AFK_h':]

AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  \
1         0      0      0      0      0      0      0      0      0      0   
2         1      0      0      0      0      1      0      0      0      0   
3         1      0      0      2      1      2      0      0      0      0   
4         1      0      0      0      1      0      0      0      0      0   
5         0      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      1      0      1      0      5      3      0      0      1      0   
2016      2      0      0      0     10     13      0      0      0      0   
2017      0      0      0      0      3      0      0      0      0      0   
2018      0      0      0      0      4      0      0      0      2      0   
2019      1      0      1      0     12     14      0      0      8      0   

      CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  \
1         0      2      0      0      0      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         1      0      1      0      0      1      1      3      1      0   
4         1      0      0      0      0      0      0      2      1      0   
5         0      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0     12     10      0      0      1      0      0      0      0   
2016      1     20     20      0      0      1      0      1      3      0   
2017      0      2      8      0      0      0      0      1      0      0   
2018      1      2      2      0      0      1      0      0      0      0   
2019      0     36     25      0      2      2      0      2      3      1   

      EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  \
1         0      0      0      0      0      0      0      0      0      0   
2         0      1      0      0      0      0      0      0      0      0   
3         0      1      0      0      0      0      0      0      0      0   
4         0      0      0      0      0      0      0      0      0      0   
5         0      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      2      0      0      4      0      0      0      3      2   
2016      0     15      0      0      5      0      0      0      1      7   
2017      0      6      0      0      1      1      0      0      0      7   
2018      0      1      0      0      1      1      0      0      0      0   
2019      0      4      0      0     13      5      1      0      3     11   

      HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  \
1         0      0      1      0      0      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         0      1      1      1      0      2      0      0      0      0   
4         0      0      1      0      0      0      0      0      0      0   
5         0      0      1      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      0      1      0      0      1     10      3      0      0   
2016      0      1      2      0      1      1      6      2      0      0   
2017      0      0      0      1      0      0      2      0      0      0   
2018      0      0      0      0      0      0      1      0      0      0   
2019      0      2      2      2      0      5     19      0      0      0   

      KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  MID_h  MLC_h  MMT_h  \
1         0      0      1      1      0      0      1      1      1      1   
2         0      0      0      3      0      0      0      0      1      0   
3         1      0      

In [109]:
sdf_LEHDCommutePatterns

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid  AFK_h  ALA_h  \
0     {'rings': [[[429468.0213051503, 4496405.233871...     668     10      1   
1     {'rings': [[[430494.91099986027, 4495540.43917...     669      0      0   
2     {'rings': [[[425457.5579433697, 4507873.987348...     670      0      0   
3     {'rings': [[[425448.36375707807, 4507253.27157...     671      1      0   
4     {'rings': [[[425435.2029181655, 4506380.698648...     672      0      0   
...                                                 ...     ...    ...    ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...    1887      0      0   
2015  {'rings': [[[417490.98019006505, 4562356.17136...    1891      0      0   
2016  {'rings': [[[418380.1807087121, 4562347.716705...    1892      7      0   
2017  {'rings': [[[418871.13447070273, 4563020.29370...    1894      0      0   
2018  {'rings': [[[419571.11778565514, 4563028.08038...    1893      0      0   

      ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  \
0         2     10      0     39      0      0     10      0      0      9   
1         0      0      0      1      0      0      2      0      0      0   
2         1      0      1      1      0      0      1      0      0      0   
3         0      0      0      1      0      0      1      0      0      0   
4         0      0      0      0      0      0      0      0      1      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2014      0      0      1      2      0      0      2      0      0      9   
2015      0      1 

In [110]:
df_LEHDCommutePatterns.iloc[0,2:218]

AFK_h     12283
ALA_h       162
ALP_h      4439
BDL_h      6482
BGM_h      9819
          ...  
z49_w    233966
z51_h     11737
z51_w      7438
z57_h    107909
z57_w    100189
Name: 0, Length: 216, dtype: object

In [111]:
#initialize Percent_SA distribution dataframe
df_LEHDCommutePatterns_Percent_SA = df_LEHDCommutePatterns

#divide columns AFK_x and after by first row (totals) and columns 2:218
df_LEHDCommutePatterns_Percent_SA.loc[1:,'AFK_h':] = df_LEHDCommutePatterns.loc[1:,'AFK_h':].div(df_LEHDCommutePatterns.iloc[0,2:218])
df_LEHDCommutePatterns_Percent_SA.loc[1:,'AFK_h':] = df_LEHDCommutePatterns.loc[1:,'AFK_h':] * 100
df_LEHDCommutePatterns_Percent_SA

fakeid         GEOID     AFK_h ALA_h     ALP_h     BDL_h     BGM_h  \
0          0        colSUM     12283   162      4439      6482      9819   
1          0  490011001001       0.0   0.0       0.0       0.0       0.0   
2          1  490011001002  0.008141   0.0       0.0       0.0       0.0   
3          2  490011001003  0.008141   0.0       0.0  0.030855  0.010184   
4          3  490011002001  0.008141   0.0       0.0       0.0  0.010184   
...      ...           ...       ...   ...       ...       ...       ...   
2015    2014  490572112021  0.008141   0.0  0.022528       0.0  0.050922   
2016    2015  490572112022  0.016283   0.0       0.0       0.0  0.101843   
2017    2016  490572112023       0.0   0.0       0.0       0.0  0.030553   
2018    2017  490572112024       0.0   0.0       0.0       0.0  0.040737   
2019    2018  490572112025  0.008141   0.0  0.022528       0.0  0.122212   

         BNT_h BRT_h CDF_h     CEN_h CHA_h     CHL_h     CLF_h     CLI_h  \
0        19759    71   322      7303   252      4420     13201      9986   
1          0.0   0.0   0.0       0.0   0.0       0.0   0.01515       0.0   
2     0.005061   0.0   0.0       0.0   0.0       0.0       0.0       0.0   
3     0.010122   0.0   0.0       0.0   0.0  0.022624       0.0  0.010014   
4          0.0   0.0   0.0       0.0   0.0  0.022624       0.0       0.0   
...        ...   ...   ...       ...   ...       ...       ...       ...   
2015  0.015183   0.0   0.0  0.013693   0.0       0.0  0.090902   0.10014   
2016  0.065793   0.0   0.0       0.0   0.0  0.022624  0.151504   0.20028   
2017       0.0   0.0   0.0       0.0   0.0       0.0   0.01515  0.080112   
2018       0.0   0.0   0.0  0.027386   0.0  0.022624   0.01515  0.020028   
2019  0.070854   0.0   0.0  0.109544   0.0       0.0  0.272707   0.25035   

     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h    ELK_h EMT_h  \
0      462       759     16463       543     22021     14490     1554   737   
1      0.0       0.0       0.0       0.0       0.0       0.0      0.0   0.0   
2      0.0       0.0       0.0       0.0       0.0       0.0      0.0   0.0   
3      0.0       0.0  0.006074  0.184162  0.013623  0.006901      0.0   0.0   
4      0.0       0.0       0.0       0.0  0.009082  0.006901      0.0   0.0   
...    ...       ...       ...       ...       ...       ...      ...   ...   
2015   0.0       0.0  0.006074       0.0       0.0       0.0      0.0   0.0   
2016   0.0       0.0  0.006074       0.0  0.004541  0.020704      0.0   0.0   
2017   0.0       0.0       0.0       0.0  0.004541       0.0      0.0   0.0   
2018   0.0       0.0  0.006074       0.0       0.0       0.0      0.0   0.0   
2019   0.0  0.263505  0.012148       0.0  0.009082  0.020704  0.06435   0.0   

         FAR_h FCS_h FFD_h     FRR_h     FTH_h     GLA_h GOS_h     GRL_h  \
0         9204   443    79      3038      2167       805   484      5114   
1          0.0   0.0   0.0       0.0       0.0       0.0   0.0       0.0   
2     0.010865   0.0   0.0       0.0       0.0       0.0   0.0       0.0   
3     0.010865   0.0   0.0       0.0       0.0       0.0   0.0       0.0   
4          0.0   0.0   0.0       0.0       0.0       0.0   0.0       0.0   
...        ...   ...   ...       ...       ...       ...   ...       ...   
2015   0.02173   0.0   0.0  0.131666       0.0       0.0   0.0  0.058662   
2016  0.162973   0.0   0.0  0.164582       0.0       0.0   0.0  0.019554   
2017  0.065189   0.0   0.0  0.032916  0.046147       0.0   0.0       0.0   
2018  0.010865   0.0   0.0  0.032916  0.046147       0.0   0.0       0.0   
2019  0.043459   0.0   0.0  0.427913  0.230734  0.124224   0.0  0.058662   

         HAR_h HDT_h     HEB_h     HER_h     HGH_h    HNF_h     HOL_h  \
0         3029   338      8019     16868      7738      358     14254   
1          0.0   0.0       0.0  0.005928       0.0      0.0       0.0   
2          0.0   0.0       0.0       0.0       0.0      0.0       0.0   
3          0.0   0.0   0.0

In [112]:
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_LEHDCommutePatterns_Percent_SA = pd.DataFrame.merge(sdf_BlockGroups, df_LEHDCommutePatterns_Percent_SA, on='GEOID')
sdf_LEHDCommutePatterns_Percent_SA

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid     AFK_h  \
0     {'rings': [[[429468.0213051503, 4496405.233871...     668  0.081413   
1     {'rings': [[[430494.91099986027, 4495540.43917...     669       0.0   
2     {'rings': [[[425457.5579433697, 4507873.987348...     670       0.0   
3     {'rings': [[[425448.36375707807, 4507253.27157...     671  0.008141   
4     {'rings': [[[425435.2029181655, 4506380.698648...     672       0.0   
...                                                 ...     ...       ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...    1887       0.0   
2015  {'rings': [[[417490.98019006505, 4562356.17136...    1891       0.0   
2016  {'rings': [[[418380.1807087121, 4562347.716705...    1892  0.056989   
2017  {'rings': [[[418871.13447070273, 4563020.29370...    1894       0.0   
2018  {'rings': [[[419571.11778565514, 4563028.08038...    1893       0.0   

         ALA_h     ALP_h     BDL_h     BGM_h     BNT_h BRT_h CDF_h     CEN_h  \
0     0.617284  0.045055  0.154273       0.0  0.197378   0.0   0.0   0.13693   
1          0.0       0.0       0.0       0.0  0.005061   0.0   0.0  0.027386   
2          0.0  0.022528       0.0  0.010184  0.005061   0.0   0.0  0.013693   
3          0.0       0.0       0.0       0.0  0.005061   0.0   0.0  0.013693   
4          0.0       0.0       0.0       0.0       0.0   0.0   0.0       0.0   
...        ...       ...       ...       ...       ...   ...   ...       ...   
2014       0.0       0.0       0.0  0.010184  0.010122   0.0   0.0  0.027386   
2015       0.0       0.0  0.015427  0.183318  0.025

In [113]:
sdf_LEHDCommutePatterns_Percent_SA.sum()

FID                                                   2037947
STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0350350350350350350350570350350350350570570570...
TRACTCE     1113061113061114001114001114001114001114002002...
DISTSML                                              163121.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 234, dtype: object

In [114]:
##create map centered on Salt Lake
##map_areas = gis.map('Salt Lake')
#
##define sdf layer
##sdf_LEHDCommutePatterns_Percent_SA.spatial.plot(map_widget = map_areas,
#                            renderer_type='s',
#                            cmap = 'RdPu',  # use a red to purple color map
#                            symbol_type='simple',
#                            outline_style='s',
#                            outline_color=[0,0,0,255],
#                            line_width=1.0)
#
##display map
#map_areas

In [115]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Number)
sdf_LEHDCommutePatterns.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Number)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\BlockGroup_CommutePatterns_Number'

In [116]:
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_SA)
sdf_LEHDCommutePatterns_Percent_SA.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_SA)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\BlockGroup_CommutePatterns_Percent_SelectedArea'

# Group by Tract

In [117]:
#input filenames
fname_Tracts_shp = os.path.join(dirInput, 'Utah_Census_Tracts_2020' + r'\CensusTracts2020.shp')

In [118]:
#read tract shapefile
sdf_Tracts = pd.DataFrame.spatial.from_featureclass(fname_Tracts_shp)
sdf_Tracts

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE  
0    {"rings": [[[-12434548.4857, 4911361.749799997...  
1    {"rings": [[[-12429589.868, 4898990.177699998]...  
2    {"rings": [[[-12439397.559799999, 4872289.2984...  
3    {"rings": [[[-12442557.703499999, 4926512.4487...  
4    {"rings": [[[-12437368.7665, 4920654.352499999...  
..                                                 ...  
711  {"rings": [[[-12455347.0952, 4966754.840000004...  
712  {"rings": [[[-12453471.3611, 4964642.738300003...  
713  {"rings": [[[-12454528.1172, 4964343.751500003...  
714  {"rings": [[[-12465233.158599999, 4967696.3889...  
715  {"rings": [[[-12390649.8356, 4669994.337099999...  

[716 rows x 17 columns]

In [119]:
#calculate tract stats
df_LEHDCommutePatterns_tract = sdf_LEHDCommutePatterns.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_tract = df_LEHDCommutePatterns_tract.reset_index()
display(df_LEHDCommutePatterns_tract)

#caclulate tract Percent_SA stats
df_LEHDCommutePatterns_Percent_SA_tract = sdf_LEHDCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_Percent_SA_tract = df_LEHDCommutePatterns_Percent_SA_tract.reset_index()
display(df_LEHDCommutePatterns_Percent_SA_tract)


#df_test = df_LEHDCommutePatterns / df_LEHDCommutePatterns_ColSum

STATEFP COUNTYFP TRACTCE  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0        49      001  100100      2      0      0      2      1      3      0   
1        49      001  100200      1      0      0      0      2      0      0   
2        49      003  960100      0      0      0      0     56      4      0   
3        49      003  960200      1      0      0      0    185      2      0   
4        49      003  960301      0      0      0      0     79      3      0   
..      ...      ...     ...    ...    ...    ...    ...    ...    ...    ...   
711      49      057  210900      4      0      0      1     14     38      0   
712      49      057  211000      0      0      0      0      1      1      0   
713      49      057  211100      2      0      1      0     44     39      0   
714      49      057  211201      0      0      0      1     11     10      0   
715      49      057  211202      4      0      2      0     34     30      0   

     CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0        0      0      0      1      2      1      0      0      1      1   
1        0      0      0      1      0      0      0      0      2      0   
2        0      4      0      0      7      4      0      0      1      0   
3        0      1      0      0     11      6      0      0      0      0   
4        0      0      0      0      4      1      0      0      3      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0     14      0      0     47     47      0      2     12      0   
712      0      1      0      0     11      4      0      0      0      0   
713      0     10      0      1     71     97      0      3      2      2   
714      0      4      1      1     18     23      0      0      5      0   
715      0     11      0      2     72     65      0      2      5      0   

     DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0        3      1      0      0      2      0      0      0      0      0   
1        2      1      0      0      0      0      0      0      0      0   
2        3      1      0      0      2      0      0      6      0      0   
3        3      0      0      0      1      0      0      5      1      1   
4        2      1      0      0      0      0      0      4      1      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      9      5      1      1     11      0      0     16      6      1   
712      0      0      0      0      0      0      0     10      2      1   
713      8      5      0      0     14      0      0     57     12      0   
714      3      1      0      0      8      0      0     15      2      0   
715      4      6      1      0     28      0      0     24      7      1   

     GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0        0      0      0      0      1      2      1      0      2      0   
1        0      1      0      0      0      3      0      0      0      0   
2        0      1      4      0      2      3      1      0      0      6   
3        0      4      0      0      3      2      1      0      0      1   
4        0      4      3      0      0      0      1      0      2      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0      7     19      0      3      8      1      0     14     15   
712      0      0      6      0      0      0      0      0      0      1   
713      1      0     56      0      5      2      2      3      6     75   
714      0      0     12      0      1      0      0      0      4      8   
715      0      7     27      0      3      5      3      1      7     38   

     HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0        0      0      0      1      0      3      6      1      0      2   
1        0      0      0      0      0      1      0      3      0      0   
2        0      0      0 

STATEFP COUNTYFP TRACTCE     AFK_h  ALA_h     ALP_h     BDL_h     BGM_h  \
0        49      001  100100  0.016283    0.0  0.000000  0.030855  0.010184   
1        49      001  100200  0.008141    0.0  0.000000  0.000000  0.020369   
2        49      003  960100  0.000000    0.0  0.000000  0.000000  0.570323   
3        49      003  960200  0.008141    0.0  0.000000  0.000000  1.884102   
4        49      003  960301  0.000000    0.0  0.000000  0.000000  0.804563   
..      ...      ...     ...       ...    ...       ...       ...       ...   
711      49      057  210900  0.032565    0.0  0.000000  0.015427  0.142581   
712      49      057  211000  0.000000    0.0  0.000000  0.000000  0.010184   
713      49      057  211100  0.016283    0.0  0.022528  0.000000  0.448111   
714      49      057  211201  0.000000    0.0  0.000000  0.015427  0.112028   
715      49      057  211202  0.032565    0.0  0.045055  0.000000  0.346267   

        BNT_h  BRT_h  CDF_h     CEN_h     CHA_h     CHL_h     CLF_h     CLI_h  \
0    0.015183    0.0    0.0  0.000000  0.000000  0.022624  0.015150  0.010014   
1    0.000000    0.0    0.0  0.000000  0.000000  0.022624  0.000000  0.000000   
2    0.020244    0.0    0.0  0.054772  0.000000  0.000000  0.053026  0.040056   
3    0.010122    0.0    0.0  0.013693  0.000000  0.000000  0.083327  0.060084   
4    0.015183    0.0    0.0  0.000000  0.000000  0.000000  0.030301  0.010014   
..        ...    ...    ...       ...       ...       ...       ...       ...   
711  0.192317    0.0    0.0  0.191702  0.000000  0.000000  0.356034  0.470659   
712  0.005061    0.0    0.0  0.013693  0.000000  0.000000  0.083327  0.040056   
713  0.197378    0.0    0.0  0.136930  0.000000  0.022624  0.537838  0.971360   
714  0.050610    0.0    0.0  0.054772  0.396825  0.022624  0.136353  0.230322   
715  0.151830    0.0    0.0  0.150623  0.000000  0.045249  0.545413  0.650911   

     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h    ELK_h  \
0      0.0  0.000000  0.006074  0.184162  0.013623  0.006901  0.00000   
1      0.0  0.000000  0.012148  0.000000  0.009082  0.006901  0.00000   
2      0.0  0.000000  0.006074  0.000000  0.013623  0.006901  0.00000   
3      0.0  0.000000  0.000000  0.000000  0.013623  0.000000  0.00000   
4      0.0  0.000000  0.018223  0.000000  0.009082  0.006901  0.00000   
..     ...       ...       ...       ...       ...       ...      ...   
711    0.0  0.263505  0.072891  0.000000  0.040870  0.034507  0.06435   
712    0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.00000   
713    0.0  0.395257  0.012148  0.368324  0.036329  0.034507  0.00000   
714    0.0  0.000000  0.030371  0.000000  0.013623  0.006901  0.00000   
715    0.0  0.263505  0.030371  0.000000  0.018164  0.041408  0.06435   

        EMT_h     FAR_h  FCS_h  FFD_h     FRR_h     FTH_h     GLA_h     GOS_h  \
0    0.000000  0.021730    0.0    0.0  0.000000  0.000000  0.000000  0.000000   
1    0.000000  0.000000    0.0    0.0  0.000000  0.000000  0.000000  0.000000   
2    0.000000  0.021730    0.0    0.0  0.197498  0.000000  0.000000  0.000000   
3    0.000000  0.010865    0.0    0.0  0.164582  0.046147  0.124224  0.000000   
4    0.000000  0.000000    0.0    0.0  0.131666  0.046147  0.000000  0.000000   
..        ...       ...    ...    ...       ...       ...       ...       ...   
711  0.135685  0.119513    0.0    0.0  0.526662  0.276880  0.124224  0.000000   
712  0.000000  0.000000    0.0    0.0  0.329164  0.092293  0.124224  0.000000   
713  0.000000  0.152108    0.0    0.0  1.876234  0.553761  0.000000  0.206612   
714  0.000000  0.086919    0.0    0.0  0.493746  0.092293  0.000000  0.000000   
715  0.000000  0.304216    0.0    0.0  0.789993  0.323027  0.124224  0.000000   

        GRL_h     HAR_h  HDT_h     HEB_h     HER_h     HGH_h     HNF_h  \
0    0.000000  0.000000    0.0  0.012470  0.011857  0.012923  0.000000   
1    0.019554  0.000000    0.0  0.000000  0.017785  0.000000  0.000000   
2    0.019

In [120]:
df_LEHDCommutePatterns_Percent_SA_tract.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010010030030030030030030030030030030030030050...
TRACTCE     1001001002009601009602009603019603029604009605...
AFK_h                                                   100.0
ALA_h                                                   100.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 219, dtype: object

In [121]:
sdf_LEHDCommutePatterns_tract = pd.DataFrame.merge(sdf_Tracts, df_LEHDCommutePatterns_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_LEHDCommutePatterns_tract)

sdf_LEHDCommutePatterns_Percent_SA_tract = pd.DataFrame.merge(sdf_Tracts, df_LEHDCommutePatterns_Percent_SA_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_LEHDCommutePatterns_Percent_SA_tract)

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0    000901     65      0     21     11     14     16      0      1      2   
1    002500     30      0      2      3      0      1      0      0      0   
2    003401      9      0      1      0      2      3      0      0      1   
3    010210     26      0      9      1      1      0      0      0      1   
4    000505     13      0      6      0      1      1      0      0      2   
..      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711  111701      4      0      1      4      2     27      0      0     10   
712  111903     33      2    

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE     AFK_h     ALA_h     ALP_h     BDL_h     BGM_h     BNT_h  \
0    000901  0.529187  0.000000  0.473080  0.169701  0.142581  0.080976   
1    002500  0.244240  0.000000  0.045055  0.046282  0.000000  0.005061   
2    003401  0.073272  0.000000  0.022528  0.000000  0.020369  0.015183   
3    010210  0.211675  0.000000  0.202748  0.015427  0.010184  0.000000   
4    000505  0.105837  0.000000  0.135166  0.000000  0.010184  0.005061   
..      ...       ...       ...       ...       ...       ...       ...   
711  111701  0.032565  0.000000  0.022528  0.061709  0.020369  0.136647   
712  111903  0.268664  1.234568  0.608245  0.586239  

In [122]:
sdf_LEHDCommutePatterns_tract.sum()


FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_w                                                    233966
z51_h                                                     11737
z51_w                                                      7438
z57_h                                                    107909
z57_w                                                    100189
Length: 235, dtype: object

In [123]:
sdf_LEHDCommutePatterns_Percent_SA_tract.sum()

FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_w                                                     100.0
z51_h                                                     100.0
z51_w                                                     100.0
z57_h                                                     100.0
z57_w                                                     100.0
Length: 235, dtype: object

In [124]:
sdf_LEHDCommutePatterns_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Number)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\Tract_CommutePatterns_Number'

In [125]:
sdf_LEHDCommutePatterns_Percent_SA_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_SA)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\Tract_CommutePatterns_Percent_SelectedArea'

# Group by Small District

In [126]:
#input filenames
fname_SD_shp = os.path.join(dirInput, 'Dist_Small' + r'\Dist_Small_Counties.shp')

In [127]:
sdf_SD = pd.DataFrame.spatial.from_featureclass(fname_SD_shp)
sdf_SD

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      4      5.0                      4.1: Willard        49        003   
..   ...      ...                               ...       ...        ...   
150  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
151  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
152  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
153  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
154  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE  
0    {"rings": [[[412988.500000001, 4605724.4], [41...  
1    {"rings": [[[408196.8937999996, 4599532.781500...  
2    {"rings": [[[413636.79999999964, 4598064.69999...  
3    {"rings": [[[415302.1999999995, 4598736.699999...  
4    {"rings": [[[412551.0000000001, 4588753.600000...  
..                                                 ...  
150  {"rings": [[[384022.18659999967, 4263333.3738]...  
151  {"rings": [[[292688.5865000002, 4224956.9639],...  
152  {"rings": [[[438313.3267000001, 4262656.513800...  
153  {"rings": [[[609343.4170000004, 4095382.083499...  
154  {"rings": [[[425313.8965999996, 4154648.073699...  

[155 rows x 6 columns]

In [128]:
#calculate small district stats
df_LEHDCommutePatterns_sd = sdf_LEHDCommutePatterns.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_sd = df_LEHDCommutePatterns_sd.reset_index()
display(df_LEHDCommutePatterns_sd)

#caclulate tract Percent_SA stats
df_LEHDCommutePatterns_Percent_SA_sd = sdf_LEHDCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_Percent_SA_sd = df_LEHDCommutePatterns_Percent_SA_sd.reset_index()
display(df_LEHDCommutePatterns_Percent_SA_sd)


#df_test = df_LEHDCommutePatterns / df_LEHDCommutePatterns_ColSum

STATEFP COUNTYFP  DISTSML  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  \
0        49      001    149.0      3      0      0      2      3      3   
1        49      003      1.0      1      0      0      0    190      1   
2        49      003      2.0      1      0      0      0     35      3   
3        49      003      3.0      7      0      0      2    649     11   
4        49      003      4.0      4      0      2      2   1852     16   
..      ...      ...      ...    ...    ...    ...    ...    ...    ...   
143      49      057     17.0     24      0      9      7    168    148   
144      49      057     18.0     28      0      6      5    101    154   
145      49      057     19.0      1      0      0      0     23     55   
146      49      057    124.0      1      0      0      0     33      3   
147      49      057    147.0      2      0      1      2     12     10   

     BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  \
0        0      0      0      0      2      2      1      0      0      3   
1        0      0      1      0      0     13      4      0      1      0   
2        0      0      2      0      0      4      3      0      0      0   
3        0      0      1      0      3     17      5      0      0      3   
4        0      0      5      0      4     46     25      0      2      8   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      0      0     48      0     12    433    423      2      7     34   
144      0      0     59      1     13    236    269      0      7     43   
145      0      0     12      0      0     44     65      0      1      2   
146      0      0      0      0      0     25     40      0      2      3   
147      0      0     19      1      0     27     32      0      1     13   

     DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  \
0        1      5      2      0      0      2      0      0      0      0   
1        0      0      1      0      0      0      0      0      4      0   
2        0      1      0      0      0      0      0      0      2      0   
3        0      2      2      0      0      1      0      0     10      2   
4        0     12      4      1      1      6      0      0     27      4   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      2     38     31      1      3     75      2      0    144     31   
144      3     55     29      5      1     75      2      0    112     28   
145      0      1      2      0      1     25      0      0     32      4   
146      0      0      0      0      0      8      0      0     42      2   
147      1     12      3      0      2     31      0      0     14      4   

     GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  \
0        0      0      1      0      0      1      5      1      0      2   
1        0      0      0      4      1      2      0      1      0      1   
2        0      0      0      6      0      1      0      1      0      0   
3        0      0      3     22      2      0      1      1      1      5   
4        2      1      3     34      1      9      2      6      1     11   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      3      1     17    152      1     18     27     14      5     24   
144      2      1     26    124      0     33     29     18      2     46   
145      0      0      0     40      0      3      0      2      1      9   
146      0      0      1     27      0      0      0      0      0      1   
147      0      0      1     14      0      7      7      1      0     11   

     HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  \
0        0      0      0      0      1      0      4      6      4      0   
1        1      0      0      0      3      0      0     12      3      0   
2        5      0      0      0      1      0      0      2      0      0   
3       13      1   

STATEFP COUNTYFP  DISTSML     AFK_h  ALA_h     ALP_h     BDL_h      BGM_h  \
0        49      001    149.0  0.024424    0.0  0.000000  0.030855   0.030553   
1        49      003      1.0  0.008141    0.0  0.000000  0.000000   1.935024   
2        49      003      2.0  0.008141    0.0  0.000000  0.000000   0.356452   
3        49      003      3.0  0.056989    0.0  0.000000  0.030855   6.609634   
4        49      003      4.0  0.032565    0.0  0.045055  0.030855  18.861391   
..      ...      ...      ...       ...    ...       ...       ...        ...   
143      49      057     17.0  0.195392    0.0  0.202748  0.107991   1.710969   
144      49      057     18.0  0.227957    0.0  0.135166  0.077137   1.028618   
145      49      057     19.0  0.008141    0.0  0.000000  0.000000   0.234240   
146      49      057    124.0  0.008141    0.0  0.000000  0.000000   0.336083   
147      49      057    147.0  0.016283    0.0  0.022528  0.030855   0.122212   

        BNT_h  BRT_h  CDF_h     CEN_h     CHA_h     CHL_h     CLF_h     CLI_h  \
0    0.015183    0.0    0.0  0.000000  0.000000  0.045249  0.015150  0.010014   
1    0.005061    0.0    0.0  0.013693  0.000000  0.000000  0.098477  0.040056   
2    0.015183    0.0    0.0  0.027386  0.000000  0.000000  0.030301  0.030042   
3    0.055671    0.0    0.0  0.013693  0.000000  0.067873  0.128778  0.050070   
4    0.080976    0.0    0.0  0.068465  0.000000  0.090498  0.348458  0.250350   
..        ...    ...    ...       ...       ...       ...       ...       ...   
143  0.749026    0.0    0.0  0.657264  0.000000  0.271493  3.280055  4.235930   
144  0.779392    0.0    0.0  0.807887  0.396825  0.294118  1.787743  2.693771   
145  0.278354    0.0    0.0  0.164316  0.000000  0.000000  0.333308  0.650911   
146  0.015183    0.0    0.0  0.000000  0.000000  0.000000  0.189380  0.400561   
147  0.050610    0.0    0.0  0.260167  0.396825  0.000000  0.204530  0.320449   

      CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h    ELK_h  \
0    0.0000  0.000000  0.018223  0.184162  0.022706  0.013803  0.00000   
1    0.0000  0.131752  0.000000  0.000000  0.000000  0.006901  0.00000   
2    0.0000  0.000000  0.000000  0.000000  0.004541  0.000000  0.00000   
3    0.0000  0.000000  0.018223  0.000000  0.009082  0.013803  0.00000   
4    0.0000  0.263505  0.048594  0.000000  0.054493  0.027605  0.06435   
..      ...       ...       ...       ...       ...       ...      ...   
143  0.4329  0.922266  0.206524  0.368324  0.172563  0.213941  0.06435   
144  0.0000  0.922266  0.261192  0.552486  0.249762  0.200138  0.32175   
145  0.0000  0.131752  0.012148  0.000000  0.004541  0.013803  0.00000   
146  0.0000  0.263505  0.018223  0.000000  0.000000  0.000000  0.00000   
147  0.0000  0.131752  0.078965  0.184162  0.054493  0.020704  0.00000   

        EMT_h     FAR_h     FCS_h  FFD_h     FRR_h     FTH_h     GLA_h  \
0    0.000000  0.021730  0.000000    0.0  0.000000  0.000000  0.000000   
1    0.000000  0.000000  0.000000    0.0  0.131666  0.000000  0.000000   
2    0.000000  0.000000  0.000000    0.0  0.065833  0.000000  0.000000   
3    0.000000  0.010865  0.000000    0.0  0.329164  0.092293  0.000000   
4    0.135685  0.065189  0.000000    0.0  0.888743  0.184587  0.248447   
..        ...       ...       ...    ...       ...       ...       ...   
143  0.407056  0.814863  0.451467    0.0  4.739961  1.430549  0.372671   
144  0.135685  0.814863  0.451467    0.0  3.686636  1.292109  0.248447   
145  0.135685  0.271621  0.000000    0.0  1.053325  0.184587  0.000000   
146  0.000000  0.086919  0.000000    0.0  1.382488  0.092293  0.000000   
147  0.271370  0.336810  0.000000    0.0  0.460829  0.184587  0.000000   

        GOS_h     GRL_h     HAR_h     HDT_h     HEB_h     HER_h     HGH_h  \
0    0.000000  0.019554  0.000000  0.000000  0.012470  0.029642  0.012923   
1    0.000000  0.000000  0.132057  0.295858  0.024941  0.000000  0.012923   
2    0.000000  0.000000  0.198085  0.000000  0.01

In [129]:
df_LEHDCommutePatterns_Percent_SA_sd.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010030030030030030030030050070090110110110110...
DISTSML                                               11772.0
AFK_h                                                   100.0
ALA_h                                                   100.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 219, dtype: object

In [130]:
sdf_LEHDCommutePatterns_sd = pd.DataFrame.merge(sdf_SD, df_LEHDCommutePatterns_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_LEHDCommutePatterns_sd)

sdf_LEHDCommutePatterns_Percent_SA_sd = pd.DataFrame.merge(sdf_SD, df_LEHDCommutePatterns_Percent_SA_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_LEHDCommutePatterns_Percent_SA_sd)

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

     AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  \
0        1      0      0      0    190      1      0      0      1      0   
1        1      0      0      0     35      3      0      0      2      0   
2        7      0      0      2    649     11      0      0      1      0   
3        4      0      2      2   1852     16      0      0      5      0   
4        0      0      0      0     38      0      0      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      0      0      0      0      0      0      0      0      0   
143     23      0     17      3     20      9      0      0      7      0   
144      0      0      1      1      3      1      0      0      0      0   
145      3      0      2      0      6      3      0      0      2      0   
146      4      0      2      0      0      3      0      0      1      0   

     CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  \
0        0     13      4      0      1      0      0      0      1      0   
1        0      4      3      0      0      0      0      1      0      0   
2        3     17      5      0      0      3      0      2      2      0   
3        4     46     25      0      2      8      0     12      4      1   
4        1      0      0      0      0      0      0      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      1      0      0      0      0      0      1      1      0   
143      6      9      7      1      0     12      0     24     24      4   
144      0      1      1      0      0      1      0      1      1      0   
145      1      2      2      0      0      4      0      4      4      2   
146      4      3      0      0      0      5      0      0      2      0   

     EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  \
0        0      0      0      0      4      0      0      0      0      4   
1        0      0      0      0      2      0      0      0      0      6   
2        0      1      0      0     10      2      0      0      3     22   
3        1      6      0      0  

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

        AFK_h  ALA_h     ALP_h     BDL_h      BGM_h     BNT_h  BRT_h  CDF_h  \
0    0.008141    0.0  0.000000  0.000000   1.935024  0.005061    0.0    0.0   
1    0.008141    0.0  0.000000  0.000000   0.356452  0.015183    0.0    0.0   
2    0.056989    0.0  0.000000  0.030855   6.609634  0.055671    0.0    0.0   
3    0.032565    0.0  0.045055  0.030855  18.861391  0.080976    0.0    0.0   
4    0.000000    0.0  0.000000  0.000000   0.387005  0.000000    0.0    0.0   
..        ...    ...       ...       ...        ...       ...    ...    ...   
142  0.000000    0.0  0.000000  0.000000   0.000000  0.000000    0.0    0.0   
143  0.187251    0.0  0.382969  0.046282   0.203687  0.045549    0.0    0.0   
144  0.000000    0.0  0.022528  0.015427   0.030553  0.005061    0.0    0.0   
145  0.024424    0.0  0.045055  0.000000   0.061106  0.015183    0.0    0.0   
146  0.032565    0.0  0.045055  0.000000   0.000000  0.015183    0.0    0.0   

        CEN_h  CHA_h     CHL_h     CLF_h     CLI_h    CMT_h     COA_h  \
0    0.013693    0.0  0.000000  0.098477  0.040056  0.00000  0.131752   
1    0.027386    0.0  0.000000  0.030301  0.030042  0.00000  0.000000   
2    0.013693    0.0  0.067873  0.128778  0.050070  0.00000  0.000000   
3    0.068465    0.0  0.090498  0.348458  0.250350  0.00000  0.263505   
4    0.000000    0.0  0.022624  0.000000  0.000000  0.00000  0.000000   
..        ...    ...       ...       ...       ...      ...       ...   
142  0.000000    0.0  0.000000  0.007575  0.000000  0.00000  0.000000   
143  0.095851    0.0  0.135747  0.068177  0.070098  0.21645  0.000000   
144  0.000000    0.0  0.000000  0.007575  0.010014  0.00000  0.000000   
145  0.027386    0.0  0.022624  0.015150  0.020028  0.00000  0.000000   
146  0.013693    0.0  0.090498  0.022726  0.000000  0.00000  0.000000   

        CWH_h  DAN_h     DRA_h     EAG_h    ELK_h     EMT_h     FAR_h  \
0    0.000000    0.0  0.000000  0.006901  0.00000  0.000000  0.000000   
1    0.000000    0.0  0.004541  0.000000  0.00000  0.000000  0.000000   
2    0.018223    0.0  0.009082  0.013803  0.00000  0.000000  0.010865   
3    0.048594    0.0  0.054493  0.027605  0.06435  0.135685  0.065189   


In [131]:
sdf_LEHDCommutePatterns_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_w                                                    233788
z51_h                                                     11737
z51_w                                                      7437
z57_h                                                    107904
z57_w                                                    100174
Length: 223, dtype: object

In [132]:
sdf_LEHDCommutePatterns_Percent_SA_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_w                                                 99.923921
z51_h                                                     100.0
z51_w                                                 99.986556
z57_h                                                 99.995366
z57_w                                                 99.985028
Length: 223, dtype: object

In [133]:
sdf_LEHDCommutePatterns_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Number)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\SD_CommutePatterns_Number'

In [134]:
sdf_LEHDCommutePatterns_Percent_SA_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Percent_SA)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\SD_CommutePatterns_Percent_SelectedArea'

# Group Rows by City

In [135]:

#verify that shape exists and sdf was created correctly and get spatial reference
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)
#
##change projection to 26912 to match TAZ Centroids
#sdf_CityTownship.spatial.project(26912)
#sdf_BlockGroups.spatial.project(26912)
#
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)

print ("Calculating blockgroup acreage...")

# Execute DeleteField
arcpy.DeleteField_management(fname_BlockGroups_shp, ['BGAcres'])

arcpy.AddField_management(fname_BlockGroups_shp, "BGAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_BlockGroups_shp,
                                "BGAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Done calculating blockgroup acreage.")


print ("Intersecting blockgroup with city/township/county...")
#intersection parcels with analysis area types
deleteIfExists(fname_CityTownshipCounty_BlockGroups_shp)
arcpy.analysis.Intersect([fname_CityTownshipCountyWCodes_shp,fname_BlockGroups_shp], fname_CityTownshipCounty_BlockGroups_shp)


print ("Calculating piece area...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PieceAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PieceAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Calculating Percent_SA of blockgroup...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PortionBG" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PortionBG",
                                "!PieceAcres!/!BGAcres!",
                                "PYTHON_9.3")


print ("Done")

Calculating blockgroup acreage...
Done calculating blockgroup acreage.
Intersecting blockgroup with city/township/county...
Calculating piece area...
Calculating Percent_SA of blockgroup...
Done


In [136]:
#read newly created shapefile
sdf_CityTownshipCounty_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipCounty_BlockGroups_shp)


In [143]:
sdf_LEHDCommutePatterns_joinCity = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_LEHDCommutePatterns,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_LEHDCommutePatterns_joinCity

FID_x  FID_Munici  Id  fid_muni_1 code3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           first_name  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [144]:
my_list = list(sdf_LEHDCommutePatterns_joinCity)
my_list

['FID_x',
 'FID_Munici',
 'Id',
 'fid_muni_1',
 'code3',
 'first_name',
 'FID_tl_202',
 'STATEFP',
 'COUNTYFP',
 'TRACTCE',
 'DISTSML',
 'BLKGRPCE',
 'GEOID',
 'NAMELSAD',
 'MTFCC',
 'FUNCSTAT',
 'ALAND',
 'AWATER',
 'INTPTLAT',
 'INTPTLON',
 'CENTROID_X_x',
 'CENTROID_Y_x',
 'BGAcres',
 'PieceAcres',
 'PortionBG',
 'SHAPE_x',
 'FID_y',
 'CENTROID_X_y',
 'CENTROID_Y_y',
 'SHAPE_y',
 'fakeid',
 'AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PG

In [49]:
#for i in dColCodes:
#    display(sdf_LEHDCommutePatterns_joinCity[[i]])

In [145]:
df_LEHDCommutePatterns_CityCalcs = sdf_LEHDCommutePatterns_joinCity.copy()

for i in dColCodesWCounty:
    display(i)
    
    df_LEHDCommutePatterns_CityCalcs[i] = df_LEHDCommutePatterns_CityCalcs[i] * df_LEHDCommutePatterns_CityCalcs['PortionBG']


'AFK_h'

'ALA_h'

'ALP_h'

'BDL_h'

'BGM_h'

...

'z49_w'

'z51_h'

'z51_w'

'z57_h'

'z57_w'

In [146]:
df_LEHDCommutePatterns_CityCalcs = df_LEHDCommutePatterns_CityCalcs.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_LEHDCommutePatterns_CityCalcs

FID_x  FID_Munici  Id  fid_muni_1 CODE3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           FIRST_NAME  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [147]:
df_LEHDCommutePatterns_CityCalcsSum = df_LEHDCommutePatterns_CityCalcs.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_CityCalcsSum = df_LEHDCommutePatterns_CityCalcsSum.reset_index()
df_LEHDCommutePatterns_CityCalcsSum

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1681      1    287   
1        1   ALA                              Alta      1      2      0   
2        2   ALP                            Alpine    115      0    303   
3        3   BDL                         Bluffdale     50      0     11   
4        4   BGM                      Brigham City      6      0      2   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    512      0    121   
122    122   z51     Wasatch County Unincorporated     10      0      2   
123    123   z53  Washington County Unincorporated     41      0     16   
124    124   z55       Wayne County Unincorporated      0      0      1   
125    125   z57       Weber County Unincorporated      1      0      0   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      127     44     96      1      8     35      2    313     47     41   
1        0      0      0      1      0      0      0      0      0      0   
2       11      3     11      0      0      2      0     58      1      5   
3      394      3     17      0      4      4      0     10      9      4   
4        2   2282     18      0      0      5      0      5     55     28   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     36     23     44      0      6     14      0    146     30     16   
122      0      5      7      0      0      0     16      1      4      0   
123      8     16     38      0      0     18      0     11     33     11   
124      1      3      1      0      0      0      0      0      1      1   
125      1    101     42      0      0     26      0      0    129    150   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        3      3     92      2    451    757     21      3     37      0   
1        0      0     40      0      8      0      0      0      1      0   
2        0      0     22      1     34     80      2      2      2      0   
3        3      0     26      1    198    134      0      0      5      0   
4        0      2      9      0     13      4      1      1      6      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      2     46      2    187    359    156      1     19      2   
122      0      4      6     41      6      8      0      0      0      2   
123      0      0     53      0     74     57      0      0     14      0   
124      0      0      1      0      1      1      0      0      0      0   
125      0      2     18      1     16      5      0      1     45      0   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        2      7      7      9      3     36      8      2     87    258   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      1      2      0     84      0      0      0     22   
3        1      0      0      1      1      9      1      0     11    163   
4        0     30      5      2      1      3     41      1      9      3   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      3      5     70     53     19      1      0     61     78   
122      0      0      1      0      0      2      0     13    641      2   
123      0      2      2      1      0      3      2      0      6     27   
124      0      0      0      0      0      0      0      0      1      2   
125      0    121      8      0      0      3     94      0     11      7   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      551      1     76     11      0      0      0     64      4     77   
1        0      0     14      0      0      0      0      0      0      2   
2      130      1     13      2      0      0      0      2      0      6   
3       30      0    

In [148]:
df_LEHDCommutePatterns_CityCalcsSum.sum()

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_h                                                     11765
ALA_h                                                       115
                                    ...                        
z49_w                                                    233127
z51_h                                                     11261
z51_w                                                      6846
z57_h                                                    107216
z57_w                                                     99357
Length: 219, dtype: object

In [149]:
sdf_LEHDCommutePatterns_joinCity_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_LEHDCommutePatterns_Percent_SA,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_LEHDCommutePatterns_joinCity_Percent_SA = sdf_LEHDCommutePatterns_joinCity_Percent_SA.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_LEHDCommutePatterns_CityCalcs_Percent_SA = sdf_LEHDCommutePatterns_joinCity_Percent_SA.copy()

for i in dColCodesWCounty:    
    df_LEHDCommutePatterns_CityCalcs_Percent_SA[i] = df_LEHDCommutePatterns_CityCalcs_Percent_SA[i] * df_LEHDCommutePatterns_CityCalcs_Percent_SA['PortionBG']


display(df_LEHDCommutePatterns_CityCalcs_Percent_SA.sum())
    
df_LEHDCommutePatterns_CityCalcs_Percent_SA = df_LEHDCommutePatterns_CityCalcs_Percent_SA.fillna(0)
   

df_LEHDCommutePatterns_CityCalcsSum_Percent_SA = df_LEHDCommutePatterns_CityCalcs_Percent_SA.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_CityCalcsSum_Percent_SA = df_LEHDCommutePatterns_CityCalcsSum_Percent_SA.reset_index()
df_LEHDCommutePatterns_CityCalcsSum_Percent_SA
    
display(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA.sum())

FID_x                                                   6578904
FID_Munici                                               251195
Id                                                            0
fid_muni_1                                               139499
CODE3         z05z03z57NOGz05z05z05z05z05z05z05z05z05z05z03z...
                                    ...                        
z49_w                                                100.067583
z51_h                                                100.071077
z51_w                                                100.070898
z57_h                                                100.063295
z57_w                                                100.062506
Length: 245, dtype: object

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_h                                                100.067534
ALA_h                                                100.066366
                                    ...                        
z49_w                                                100.067583
z51_h                                                100.071077
z51_w                                                100.070898
z57_h                                                100.063295
z57_w                                                100.062506
Length: 219, dtype: object

In [150]:
sdf_LEHDCommutePatterns_City_Number = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_LEHDCommutePatterns_CityCalcsSum,on=['CODE3','FIRST_NAME'])
sdf_LEHDCommutePatterns_City_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_LEHDCommutePatterns_CityCalcsSum_Percent_SA,on=['CODE3','FIRST_NAME'])

In [151]:
sdf_LEHDCommutePatterns_City_Number.spatial.to_featureclass(fname_CitiesWCommutePatterns_Number)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Number'

In [152]:
sdf_LEHDCommutePatterns_City_Percent_SA.spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_SA)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Percent_SelectedArea'

In [153]:
sdf_LEHDCommutePatterns_City_Number

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  index  AFK_h  ALA_h  \
0   {"rings": [[[-111.77435121873373, 40.353624868...      0   1681      1   
1   {"rings": [[[-111.59946851855727, 40.577431980...      1      1      2   
2   {"rings": [[[-111.75455302160464, 40.479513910...      2    115      0   
3   {"rings": [[[-111.9704071902396, 40.5008379065...      3     50      0   
4   {"rings": [[[-112.01898409573937, 41.535781784...      4      6      0   
..                                                ...    ...    ...    ...   
92  {"rings": [[[-112.02999503963935, 41.391465965...     92      0      0   
93  {"rings": [[[-112.00475852158849, 40.638664299...     93    121      2   
94  {"rings": [[[-112.10779328273378, 41.143687479...     94      2      0   
95  {"rings": [[[-111.9626132723846, 40.7260972067...     95    181     10   
96  {"rings": [[[-111.89260269236036, 40.866220107...     96      8      0   

    ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  \
0     287    127     44     96      1      8     35      2    313     47   
1       0      0      0      0      1      0      0      0      0      0   
2     303     11      3     11      0      0      2      0     58      1   
3      11    394      3     17      0      4      4      0     10      9   
4       2      2   2282     18      0      0      5      0      5     55   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      7      0      0      0      0      0      0      0   
93     59    353    101    215      1      6     50      4     52    125   
94      0      0      8     19      0      0     14      0      0     60   
95     98    273    155    894      2      5    359      2     84    375   
96      4      4     11    549      0      0    148      0      2     95   

    CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  \
0      41      3      3     92      2    451    757     21      3     37   
1       0      0      0     40      0      8      0      0      0      1   
2       5      0      0     22      1     34     80      2      2      2   
3       4      3      0     26      1    198    134      0      0      5   
4      28      0      2      9      0     13      4      1      1      6   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      0      0      0      0      0      0      0      0   
93     75     43      4    429      6    685    507     12     10     99   
94     83      0      0      0      0      2      2      0      0     11   
95    262     31     13    799     12    879    456     17     36    403   
96     56      0      1     34      1     39     14      0      0    198   

    FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  \
0       0      2      7      7      9      3     36      8      2     87   
1       0      0      0      0      0      0      0      0      0      0   
2       0      0      1      1      2      0     84      0      0      0   
3       0      1      0      0      1      1      9      1      0     11   
4       0      0     30      5      2      1      3     41      1      9   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      0      0      

# Calculate Percents by Map Units

In [155]:
# prepare column list

#display(dColCodesWCounty)
dColCodesWCounty = dColCodesWCounty.copy()

dColCodesWCounty_x = [x for x in dColCodesWCounty if "w" not in x]
dColCodesWCounty_y = [x for x in dColCodesWCounty if "h" not in x]

#remove and append to make sure at end
dColCodesWCounty_x.remove('TTL_h')
dColCodesWCounty_y.remove('TTL_w')
dColCodesWCounty_x.append('TTL_h')
dColCodesWCounty_y.append('TTL_w')

display(dColCodesWCounty_x)
display(dColCodesWCounty_y)

dColCodesNoTotal_x = [x for x in dColCodes if "w" not in x]
dColCodesNoTotal_x.remove('TTL_h')

dColCodesNoTotal_x = [x for x in dColCodes if "h" not in x]
dColCodesNoTotal_x.remove('TTL_w')

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'z03_h',
 'z11_h',
 'z23_h',


['AFK_w',
 'ALA_w',
 'ALP_w',
 'BDL_w',
 'BGM_w',
 'BNT_w',
 'BRT_w',
 'CDF_w',
 'CEN_w',
 'CHA_w',
 'CHL_w',
 'CLF_w',
 'CLI_w',
 'CMT_w',
 'COA_w',
 'CWH_w',
 'DAN_w',
 'DRA_w',
 'EAG_w',
 'ELK_w',
 'EMT_w',
 'FAR_w',
 'FCS_w',
 'FFD_w',
 'FRR_w',
 'FTH_w',
 'GLA_w',
 'GOS_w',
 'GRL_w',
 'HAR_w',
 'HDT_w',
 'HEB_w',
 'HER_w',
 'HGH_w',
 'HNF_w',
 'HOL_w',
 'HOO_w',
 'HVL_w',
 'IND_w',
 'INT_w',
 'KAY_w',
 'KMS_w',
 'KMT_w',
 'LAY_w',
 'LEH_w',
 'LIN_w',
 'MAP_w',
 'MID_w',
 'MLC_w',
 'MMT_w',
 'MRG_w',
 'MSL_w',
 'MUR_w',
 'MWY_w',
 'NOG_w',
 'NSL_w',
 'OGD_w',
 'OKL_w',
 'ORM_w',
 'PAY_w',
 'PGR_w',
 'PLN_w',
 'PRK_w',
 'PRY_w',
 'PVO_w',
 'PVW_w',
 'ROY_w',
 'RVD_w',
 'RVT_w',
 'SAN_w',
 'SAQ_w',
 'SAR_w',
 'SFK_w',
 'SJC_w',
 'SLC_w',
 'SLM_w',
 'SOG_w',
 'SPV_w',
 'SSL_w',
 'SUN_w',
 'SWE_w',
 'SYR_w',
 'TAY_w',
 'TOO_w',
 'UIN_w',
 'VIN_w',
 'WAT_w',
 'WBG_w',
 'WDL_w',
 'WEB_w',
 'WHT_w',
 'WHV_w',
 'WIL_w',
 'WJC_w',
 'WPT_w',
 'WVC_w',
 'WXC_w',
 'z03_w',
 'z11_w',
 'z23_w',


In [159]:
# block group
sdf_LEHDCommutePatterns_Percent_MU = sdf_LEHDCommutePatterns.copy()
sdf_LEHDCommutePatterns_tract_Percent_MU  = sdf_LEHDCommutePatterns_tract.copy()
sdf_LEHDCommutePatterns_sd_Percent_MU  = sdf_LEHDCommutePatterns_sd.copy()
sdf_LEHDCommutePatterns_City_Percent_MU  = sdf_LEHDCommutePatterns_City_Number.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    sdf_LEHDCommutePatterns_Percent_MU      [x] = sdf_LEHDCommutePatterns_Percent_MU      [x] / sdf_LEHDCommutePatterns_Percent_MU      ['TTL_h'] * 100
    sdf_LEHDCommutePatterns_tract_Percent_MU[x] = sdf_LEHDCommutePatterns_tract_Percent_MU[x] / sdf_LEHDCommutePatterns_tract_Percent_MU['TTL_h'] * 100
    sdf_LEHDCommutePatterns_sd_Percent_MU   [x] = sdf_LEHDCommutePatterns_sd_Percent_MU   [x] / sdf_LEHDCommutePatterns_sd_Percent_MU   ['TTL_h'] * 100
    sdf_LEHDCommutePatterns_City_Percent_MU [x] = sdf_LEHDCommutePatterns_City_Percent_MU [x] / sdf_LEHDCommutePatterns_City_Percent_MU ['TTL_h'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    sdf_LEHDCommutePatterns_Percent_MU      [y] = sdf_LEHDCommutePatterns_Percent_MU      [y] / sdf_LEHDCommutePatterns_Percent_MU      ['TTL_w'] * 100
    sdf_LEHDCommutePatterns_tract_Percent_MU[y] = sdf_LEHDCommutePatterns_tract_Percent_MU[y] / sdf_LEHDCommutePatterns_tract_Percent_MU['TTL_w'] * 100
    sdf_LEHDCommutePatterns_sd_Percent_MU   [y] = sdf_LEHDCommutePatterns_sd_Percent_MU   [y] / sdf_LEHDCommutePatterns_sd_Percent_MU   ['TTL_w'] * 100    
    sdf_LEHDCommutePatterns_City_Percent_MU [y] = sdf_LEHDCommutePatterns_City_Percent_MU [y] / sdf_LEHDCommutePatterns_City_Percent_MU ['TTL_w'] * 100
    

In [160]:
#check that everything is near 100 (subtracting out non-city areas)
display(sdf_LEHDCommutePatterns_Percent_MU      .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_tract_Percent_MU.loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_sd_Percent_MU   .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_City_Percent_MU .loc[:,dColCodesNoTotal_x].sum(axis=1))

0       96.056623
1       95.652174
2       97.188049
3       97.471910
4       97.443182
          ...    
2014    94.126506
2015    93.772242
2016    92.699115
2017    92.105263
2018    92.774566
Length: 2019, dtype: float64

0      96.342902
1      95.646842
2      92.147686
3      96.082546
4      96.892265
         ...    
711    96.519807
712    96.460573
713    96.696697
714    97.612958
715    20.510397
Length: 716, dtype: float64

0      79.310345
1      83.036472
2      83.151283
3      80.604357
4      80.669145
         ...    
142    24.460432
143    15.331445
144    18.479409
145     7.822686
146    10.524546
Length: 147, dtype: float64

0     91.846102
1     73.913043
2     91.082649
3     94.415523
4     79.517796
        ...    
92    64.492754
93    95.674011
94    89.859852
95    96.061955
96    90.004244
Length: 97, dtype: float64

In [161]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_MU)
deleteIfExists(fname_TractsWCommutePatterns_Percent_MU     )
deleteIfExists(fname_SDWCommutePatterns_Percent_MU         )
deleteIfExists(fname_CitiesWCommutePatterns_Percent_MU     )

sdf_LEHDCommutePatterns_Percent_MU      .spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_MU)
sdf_LEHDCommutePatterns_tract_Percent_MU.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_MU     )
sdf_LEHDCommutePatterns_sd_Percent_MU   .spatial.to_featureclass(fname_SDWCommutePatterns_Percent_MU         )
sdf_LEHDCommutePatterns_City_Percent_MU .spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_MU     )

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2018\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Percent_MapUnit'

# Summarize by County

In [162]:
df_CityTownship_NameCode

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

In [163]:
display(df_LEHDCommutePatterns_CityCalcsSum)
display(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA)

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1681      1    287   
1        1   ALA                              Alta      1      2      0   
2        2   ALP                            Alpine    115      0    303   
3        3   BDL                         Bluffdale     50      0     11   
4        4   BGM                      Brigham City      6      0      2   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    512      0    121   
122    122   z51     Wasatch County Unincorporated     10      0      2   
123    123   z53  Washington County Unincorporated     41      0     16   
124    124   z55       Wayne County Unincorporated      0      0      1   
125    125   z57       Weber County Unincorporated      1      0      0   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      127     44     96      1      8     35      2    313     47     41   
1        0      0      0      1      0      0      0      0      0      0   
2       11      3     11      0      0      2      0     58      1      5   
3      394      3     17      0      4      4      0     10      9      4   
4        2   2282     18      0      0      5      0      5     55     28   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     36     23     44      0      6     14      0    146     30     16   
122      0      5      7      0      0      0     16      1      4      0   
123      8     16     38      0      0     18      0     11     33     11   
124      1      3      1      0      0      0      0      0      1      1   
125      1    101     42      0      0     26      0      0    129    150   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        3      3     92      2    451    757     21      3     37      0   
1        0      0     40      0      8      0      0      0      1      0   
2        0      0     22      1     34     80      2      2      2      0   
3        3      0     26      1    198    134      0      0      5      0   
4        0      2      9      0     13      4      1      1      6      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      2     46      2    187    359    156      1     19      2   
122      0      4      6     41      6      8      0      0      0      2   
123      0      0     53      0     74     57      0      0     14      0   
124      0      0      1      0      1      1      0      0      0      0   
125      0      2     18      1     16      5      0      1     45      0   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        2      7      7      9      3     36      8      2     87    258   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      1      2      0     84      0      0      0     22   
3        1      0      0      1      1      9      1      0     11    163   
4        0     30      5      2      1      3     41      1      9      3   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      3      5     70     53     19      1      0     61     78   
122      0      0      1      0      0      2      0     13    641      2   
123      0      2      2      1      0      3      2      0      6     27   
124      0      0      0      0      0      0      0      0      1      2   
125      0    121      8      0      0      3     94      0     11      7   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      551      1     76     11      0      0      0     64      4     77   
1        0      0     14      0      0      0      0      0      0      2   
2      130      1     13      2      0      0      0      2      0      6   
3       30      0    

index CODE3                        FIRST_NAME      AFK_h     ALA_h  \
0        0   AFK                     American Fork  13.793384  1.219038   
1        1   ALA                              Alta   0.012556  1.409410   
2        2   ALP                            Alpine   0.955543  0.509989   
3        3   BDL                         Bluffdale   0.444319  0.000594   
4        4   BGM                      Brigham City   0.058787  0.000000   
..     ...   ...                               ...        ...       ...   
121    121   z49        Utah County Unincorporated   4.561882  0.331775   
122    122   z51     Wasatch County Unincorporated   0.156886  0.000365   
123    123   z53  Washington County Unincorporated   0.610322  0.616962   
124    124   z55       Wayne County Unincorporated   0.000003  0.000000   
125    125   z57       Weber County Unincorporated   0.057293  0.000000   

        ALP_h     BDL_h      BGM_h     BNT_h     BRT_h         CDF_h  \
0    6.698215  2.115057   0.545145  0.530703  1.409422  3.693601e+00   
1    0.013244  0.009201   0.001996  0.004053  1.859897  0.000000e+00   
2    6.916589  0.193230   0.033723  0.065961  0.000000  4.474984e-01   
3    0.357027  6.128286   0.062857  0.100936  0.001283  2.446419e+00   
4    0.045181  0.033067  23.292514  0.098665  0.000000  0.000000e+00   
..        ...       ...        ...       ...       ...           ...   
121  3.283803  0.770841   0.395372  0.341276  0.003983  3.753723e+00   
122  0.096522  0.028117   0.105249  0.060679  0.000047  4.154948e-07   
123  0.788093  0.323815   0.376653  0.328804  0.000000  6.207359e-01   
124  0.022536  0.015432   0.030572  0.005065  0.000000  0.000000e+00   
125  0.079373  0.064004   1.167744  0.279782  0.000000  3.953265e-02   

        CEN_h     CHA_h     CHL_h     CLF_h     CLI_h     CMT_h     COA_h  \
0    0.619098  2.179478  7.325610  0.430414  0.491121  0.981681  0.875395   
1    0.005133  0.000000  0.009061  0.000000  0.003754  0.000000  0.000000   
2    0.030181  0.000000  1.385906  0.014052  0.058378  0.000000  0.000000   
3    0.108451  0.344275  0.291264  0.090568  0.050774  1.242020  0.137521   
4    0.077090  0.000000  0.120098  0.438116  0.302000  0.000000  0.292331   
..        ...       ...       ...       ...       ...       ...       ...   
121  0.373084  0.882563  3.907692  0.314207  0.293480  0.896005  0.806227   
122  0.047806  8.783156  0.061626  0.068950  0.018205  0.143489  0.765349   
123  0.520086  0.396719  0.836710  0.378576  0.260239  0.000000  0.395099   
124  0.000002  0.000000  0.000006  0.007578  0.010023  0.000000  0.000000   
125  0.478390  0.566201  0.070015  1.119829  1.672587  0.065882  0.550452   

        CWH_h     DAN_h     DRA_h     EAG_h      ELK_h     EMT_h  \
0    0.609947  1.452571  2.097288  5.288612   1.792886  0.429423   
1    0.247831  0.000000  0.042442  0.002587   0.000003  0.078607   
2    0.149031  0.258951  0.169060  0.572872   0.141834  0.271559   
3    0.188838  0.366161  0.919381  0.956889   0.252828  0.407072   
4    0.058130  0.000000  0.062240  0.030105   0.064390  0.135770   
..        ...       ...       ...       ...        ...       ...   
121  0.381332  1.013795  1.010842  2.795371  11.629135  0.631745   
122  0.063523  8.850065  0.068141  0.076973   0.147949  0.129700   
123  0.528214  0.000000  0.576455  0.648414   0.257297  0.271294   
124  0.006077  0.000000  0.004544  0.006906   0.000001  0.000000   
125  0.155120  0.264780  0.111446  0.062242   0.083160  0.378720   

            FAR_h     FCS_h     FFD_h         FRR_h     FTH_h      GLA_h  \
0    4.998002e-01  0.598526  4.707485  3.062477e-01  0.362724   1.732925   
1    1.249616e-02  0.001924  0.000000  0.000000e+00  0.009043   0.000000   
2    2.730636e-02  0.000000  0.000000  3.961156e-02  0.084304   0.372605   
3    6.529256e-02  0.225276  4.863517  3.260425e-02  0.044485   0.356295   
4    6.842611e-02  0.000000  0.000000  1.070770e+00  0.243799   0.248602   
..            ...       ...       ...    

In [164]:
df_CitySum_wCounty_Join            = pd.DataFrame.merge(df_LEHDCommutePatterns_CityCalcsSum           , df_CityTownship_NameCode, on="CODE3", how="left")
df_CitySum_wCounty_Join_Percent_SA = pd.DataFrame.merge(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA, df_CityTownship_NameCode, on="CODE3", how="left")

df_CitySum_wCounty_Join           .loc[df_CitySum_wCounty_Join           .CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join           .CODE3
df_CitySum_wCounty_Join_Percent_SA.loc[df_CitySum_wCounty_Join_Percent_SA.CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join_Percent_SA.CODE3

display(df_CitySum_wCounty_Join)
display(df_CitySum_wCounty_Join_Percent_SA)

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1681      1    287   
1        1   ALA                              Alta      1      2      0   
2        2   ALP                            Alpine    115      0    303   
3        3   BDL                         Bluffdale     50      0     11   
4        4   BGM                      Brigham City      6      0      2   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    512      0    121   
122    122   z51     Wasatch County Unincorporated     10      0      2   
123    123   z53  Washington County Unincorporated     41      0     16   
124    124   z55       Wayne County Unincorporated      0      0      1   
125    125   z57       Weber County Unincorporated      1      0      0   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      127     44     96      1      8     35      2    313     47     41   
1        0      0      0      1      0      0      0      0      0      0   
2       11      3     11      0      0      2      0     58      1      5   
3      394      3     17      0      4      4      0     10      9      4   
4        2   2282     18      0      0      5      0      5     55     28   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     36     23     44      0      6     14      0    146     30     16   
122      0      5      7      0      0      0     16      1      4      0   
123      8     16     38      0      0     18      0     11     33     11   
124      1      3      1      0      0      0      0      0      1      1   
125      1    101     42      0      0     26      0      0    129    150   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        3      3     92      2    451    757     21      3     37      0   
1        0      0     40      0      8      0      0      0      1      0   
2        0      0     22      1     34     80      2      2      2      0   
3        3      0     26      1    198    134      0      0      5      0   
4        0      2      9      0     13      4      1      1      6      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      2     46      2    187    359    156      1     19      2   
122      0      4      6     41      6      8      0      0      0      2   
123      0      0     53      0     74     57      0      0     14      0   
124      0      0      1      0      1      1      0      0      0      0   
125      0      2     18      1     16      5      0      1     45      0   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        2      7      7      9      3     36      8      2     87    258   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      1      2      0     84      0      0      0     22   
3        1      0      0      1      1      9      1      0     11    163   
4        0     30      5      2      1      3     41      1      9      3   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      3      5     70     53     19      1      0     61     78   
122      0      0      1      0      0      2      0     13    641      2   
123      0      2      2      1      0      3      2      0      6     27   
124      0      0      0      0      0      0      0      0      1      2   
125      0    121      8      0      0      3     94      0     11      7   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      551      1     76     11      0      0      0     64      4     77   
1        0      0     14      0      0      0      0      0      0      2   
2      130      1     13      2      0      0      0      2      0      6   
3       30      0    

index CODE3                        FIRST_NAME      AFK_h     ALA_h  \
0        0   AFK                     American Fork  13.793384  1.219038   
1        1   ALA                              Alta   0.012556  1.409410   
2        2   ALP                            Alpine   0.955543  0.509989   
3        3   BDL                         Bluffdale   0.444319  0.000594   
4        4   BGM                      Brigham City   0.058787  0.000000   
..     ...   ...                               ...        ...       ...   
121    121   z49        Utah County Unincorporated   4.561882  0.331775   
122    122   z51     Wasatch County Unincorporated   0.156886  0.000365   
123    123   z53  Washington County Unincorporated   0.610322  0.616962   
124    124   z55       Wayne County Unincorporated   0.000003  0.000000   
125    125   z57       Weber County Unincorporated   0.057293  0.000000   

        ALP_h     BDL_h      BGM_h     BNT_h     BRT_h         CDF_h  \
0    6.698215  2.115057   0.545145  0.530703  1.409422  3.693601e+00   
1    0.013244  0.009201   0.001996  0.004053  1.859897  0.000000e+00   
2    6.916589  0.193230   0.033723  0.065961  0.000000  4.474984e-01   
3    0.357027  6.128286   0.062857  0.100936  0.001283  2.446419e+00   
4    0.045181  0.033067  23.292514  0.098665  0.000000  0.000000e+00   
..        ...       ...        ...       ...       ...           ...   
121  3.283803  0.770841   0.395372  0.341276  0.003983  3.753723e+00   
122  0.096522  0.028117   0.105249  0.060679  0.000047  4.154948e-07   
123  0.788093  0.323815   0.376653  0.328804  0.000000  6.207359e-01   
124  0.022536  0.015432   0.030572  0.005065  0.000000  0.000000e+00   
125  0.079373  0.064004   1.167744  0.279782  0.000000  3.953265e-02   

        CEN_h     CHA_h     CHL_h     CLF_h     CLI_h     CMT_h     COA_h  \
0    0.619098  2.179478  7.325610  0.430414  0.491121  0.981681  0.875395   
1    0.005133  0.000000  0.009061  0.000000  0.003754  0.000000  0.000000   
2    0.030181  0.000000  1.385906  0.014052  0.058378  0.000000  0.000000   
3    0.108451  0.344275  0.291264  0.090568  0.050774  1.242020  0.137521   
4    0.077090  0.000000  0.120098  0.438116  0.302000  0.000000  0.292331   
..        ...       ...       ...       ...       ...       ...       ...   
121  0.373084  0.882563  3.907692  0.314207  0.293480  0.896005  0.806227   
122  0.047806  8.783156  0.061626  0.068950  0.018205  0.143489  0.765349   
123  0.520086  0.396719  0.836710  0.378576  0.260239  0.000000  0.395099   
124  0.000002  0.000000  0.000006  0.007578  0.010023  0.000000  0.000000   
125  0.478390  0.566201  0.070015  1.119829  1.672587  0.065882  0.550452   

        CWH_h     DAN_h     DRA_h     EAG_h      ELK_h     EMT_h  \
0    0.609947  1.452571  2.097288  5.288612   1.792886  0.429423   
1    0.247831  0.000000  0.042442  0.002587   0.000003  0.078607   
2    0.149031  0.258951  0.169060  0.572872   0.141834  0.271559   
3    0.188838  0.366161  0.919381  0.956889   0.252828  0.407072   
4    0.058130  0.000000  0.062240  0.030105   0.064390  0.135770   
..        ...       ...       ...       ...        ...       ...   
121  0.381332  1.013795  1.010842  2.795371  11.629135  0.631745   
122  0.063523  8.850065  0.068141  0.076973   0.147949  0.129700   
123  0.528214  0.000000  0.576455  0.648414   0.257297  0.271294   
124  0.006077  0.000000  0.004544  0.006906   0.000001  0.000000   
125  0.155120  0.264780  0.111446  0.062242   0.083160  0.378720   

            FAR_h     FCS_h     FFD_h         FRR_h     FTH_h      GLA_h  \
0    4.998002e-01  0.598526  4.707485  3.062477e-01  0.362724   1.732925   
1    1.249616e-02  0.001924  0.000000  0.000000e+00  0.009043   0.000000   
2    2.730636e-02  0.000000  0.000000  3.961156e-02  0.084304   0.372605   
3    6.529256e-02  0.225276  4.863517  3.260425e-02  0.044485   0.356295   
4    6.842611e-02  0.000000  0.000000  1.070770e+00  0.243799   0.248602   
..            ...       ...       ...    

In [165]:
dColCodesWCounty

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


In [166]:
df_CountySum            = df_CitySum_wCounty_Join           .groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_Percent_SA = df_CitySum_wCounty_Join_Percent_SA.groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum            = df_CountySum           .reset_index()
df_CountySum_Percent_SA = df_CountySum_Percent_SA.reset_index()

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0      z01      2      0      0      2      2      3      0      0      0   
1      z03     21      0      2      3   3895     48      0      0     11   
2      z05     77      0     32     21    733    227      1      2     89   
3      z07     14      1     10      2     13      8      0      0      4   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11    192      2     70    117    721   6210      0      2   2551   
6      z13     12      0      8      1      4      9      0      0      6   
7      z15      3      0      4      2      3      8      0      0      3   
8      z17      2      0      1      0      0      0      0      0      2   
9      z19      3      0      4      0      3      7      0      0      1   
10     z21      7      0     10      0     10      5      0      0      2   
11     z23     25      0      8      6      2      2      0      3      1   
12     z25      4      0      1      0      0      2      0      0      1   
13     z27      7      0      2      0      3      4      0      1      3   
14     z29      1      0      1      1     11     19      0      0      6   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      2      0      1      0      2      4      0      0      0   
17     z35   2980     99   1431   4951   1507  10607     42    103   3523   
18     z37      3      0      2      0      6      3      0      0      2   
19     z39     17      0     17      1      5     20      0      1      3   
20     z41     13      0      7      3      5      8      0      0      1   
21     z43     53      5     51     32     39    130      3      0     55   
22     z45     43      1     16     18     39     76      0      3     28   
23     z47     11      0      7      4     11     25      0      1      8   
24     z49   8020      6   2303    894    419    750      2    113    246   
25     z51     59      1     12      4     21     23      0      2      9   
26     z53     41      0     16      8     16     38      0      0     18   
27     z55      0      0      1      1      3      1      0      0      0   
28     z57    153      0     57     47   1912    982      0      1    326   

    CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  \
0       0      1      2      1      0      0      3      1      4      1   
1       0     10    131     64      0      2     21      0     29     10   
2       7     25    180    102      0     16     71      2    110     75   
3       0      8      7      6      0      6     10      1     16     22   
4       0      0      0      0      0      0      0      0      0      0   
5       0     70   5311   3549     11     26    424      8    603    252   
6       1      4     15      2      0      1      8      1      7     16   
7       0      8      4      0      0      0      7      0      9     15   
8       0      1      0      1      0      0      2      0      0      2   
9       0      1      0      4      0      1      7      2     10      3   
10      0      2      4      1      0      0      6      0     13     12   
11      0      1      4      3      0      1      5      0     11     29   
12      0      3      2      0      0      0      5      0      0      1   
13      0      4      5      0      0      0      8      0     12     26   
14      0      1     38     35      0      7      4      0     16      2   
15      0      0      1      0      0      0      0      0      1      1   
16      0      0      1      1      0      0      2      0      2      1   
17     56   1313   3635   2472    317    187  13782    100  16432   6607   
18      0      1      2      2      0      0      4      0      4      4   
19      1      8     11      5      1      1     14      3     19     30   
20      0      8      2      8      0      0      7      0     13     21   
21     42     35    

zCOFIPS         AFK_h      ALA_h         ALP_h         BDL_h         BGM_h  \
0      z01  2.442601e-02   0.000000  0.000000e+00  3.086364e-02  3.055296e-02   
1      z03  2.118008e-01   0.000000  6.762391e-02  6.174752e-02  3.980374e+01   
2      z05  6.273106e-01   0.000000  7.213805e-01  3.395972e-01  7.470362e+00   
3      z07  1.140698e-01   0.617773  2.254464e-01  3.087356e-02  1.325003e-01   
4      z09  0.000000e+00   0.000000  2.248632e-02  0.000000e+00  0.000000e+00   
5      z11  1.914420e+00   2.470728  2.141491e+00  2.361889e+00  8.061086e+00   
6      z13  1.059009e-01   0.000000  2.028523e-01  1.543572e-02  4.076631e-02   
7      z15  2.444383e-02   0.000000  9.018013e-02  3.087976e-02  3.057955e-02   
8      z17  2.443284e-02   0.000000  2.255206e-02  4.286247e-06  1.114310e-05   
9      z19  2.443420e-02   0.000000  9.015280e-02  6.780167e-12  3.056532e-02   
10     z21  1.872448e-01   0.000000  3.829404e-01  4.628139e-02  2.036832e-01   
11     z23  2.323507e-01   0.000000  2.102278e-01  1.080611e-01  3.095194e-02   
12     z25  3.258317e-02   0.000000  4.505184e-02  0.000000e+00  1.035736e-07   
13     z27  5.701335e-02   0.000000  4.507330e-02  1.944855e-07  4.074556e-02   
14     z29  8.152549e-03   0.000049  2.254681e-02  1.544836e-02  1.426873e-01   
15     z31  7.111662e-09   0.000000  4.796776e-07  8.631345e-10  7.892792e-08   
16     z33  1.628937e-02   0.000000  2.253684e-02  0.000000e+00  2.038330e-02   
17     z35  2.557495e+01  83.111450  3.543444e+01  7.924371e+01  1.685591e+01   
18     z37  2.443307e-02   0.000000  4.509185e-02  2.227261e-06  6.112636e-02   
19     z39  1.385013e-01   0.000000  3.832492e-01  1.544031e-02  5.095772e-02   
20     z41  1.059026e-01   0.000000  1.577881e-01  4.630975e-02  5.095296e-02   
21     z43  5.052084e-01   3.706052  1.262273e+00  5.248837e-01  4.586643e-01   
22     z45  4.317013e-01   0.617593  4.733196e-01  3.858750e-01  4.788536e-01   
23     z47  8.960259e-02   0.000000  1.578194e-01  6.174852e-02  1.120758e-01   
24     z49  6.691256e+01   7.689969  5.486501e+01  1.528000e+01  5.054765e+00   
25     z51  6.031527e-01   0.618119  3.836799e-01  1.236121e-01  3.158868e-01   
26     z53  6.103220e-01   0.616962  7.880934e-01  3.238155e-01  3.766529e-01   
27     z55  3.417635e-06   0.000000  2.253588e-02  1.543198e-02  3.057212e-02   
28     z57  1.466323e+00   0.617671  1.780792e+00  1.003385e+00  2.017730e+01   

           BNT_h      BRT_h         CDF_h         CEN_h         CHA_h  \
0   1.518742e-02   0.000000  0.000000e+00  1.311935e-08  0.000000e+00   
1   2.785160e-01   0.000000  0.000000e+00  2.329045e-01  0.000000e+00   
2   1.149631e+00   1.409413  6.215420e-01  1.219511e+00  2.779658e+00   
3   4.051815e-02   0.000000  0.000000e+00  5.481533e-02  0.000000e+00   
4   1.473746e-07   0.000000  0.000000e+00  0.000000e+00  0.000000e+00   
5   3.194899e+01   2.818585  9.324044e-01  3.606267e+01  0.000000e+00   
6   5.569637e-02   0.000000  0.000000e+00  9.588375e-02  3.972114e-01   
7   4.052174e-02   0.000000  0.000000e+00  4.111155e-02  0.000000e+00   
8   5.062943e-03   0.000000  0.000000e+00  4.109572e-02  0.000000e+00   
9   3.543988e-02   0.000000  0.000000e+00  1.369866e-02  0.000000e+00   
10  4.554890e-02   0.000000  1.094856e-07  9.584804e-02  1.770301e-05   
11  2.633855e-02   0.000000  1.242972e+00  2.808252e-02  0.000000e+00   
12  1.518836e-02   0.000000  0.000000e+00  1.370592e-02  0.000000e+00   
13  2.025237e-02   0.000000  3.106673e-01  4.109678e-02  0.000000e+00   
14  1.121039e-01   0.000000  0.000000e+00  1.098207e-01  1.260156e-04   
15  2.344292e-07   0.000000  0.000000e+00  4.760884e-07  0.000000e+00   
16  2.025506e-02   0.000000  0.000000e+00  8.313797e-07  8.709891e-07   
17  5.467939e+01  88.787729  4.554365e+01  5.024827e+01  3.136972e+01   
18  1.518957e-02   0.000000  0.000000e+00  2.739201e-02  0.000000e+00   
19  1.012922e-01   0.000000  3.108180e-01  4.110991e-02  3.971100e-01   
20  4.051289e-02   0.000000  0.000000e+

In [167]:
df_CountySum           ['WFCounty'] = "Outside Wasatch Front"
df_CountySum_Percent_SA['WFCounty'] = "Outside Wasatch Front"

df_CountySum           .loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0      z01      2      0      0      2      2      3      0      0      0   
1      z03     21      0      2      3   3895     48      0      0     11   
2      z05     77      0     32     21    733    227      1      2     89   
3      z07     14      1     10      2     13      8      0      0      4   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11    192      2     70    117    721   6210      0      2   2551   
6      z13     12      0      8      1      4      9      0      0      6   
7      z15      3      0      4      2      3      8      0      0      3   
8      z17      2      0      1      0      0      0      0      0      2   
9      z19      3      0      4      0      3      7      0      0      1   
10     z21      7      0     10      0     10      5      0      0      2   
11     z23     25      0      8      6      2      2      0      3      1   
12     z25      4      0      1      0      0      2      0      0      1   
13     z27      7      0      2      0      3      4      0      1      3   
14     z29      1      0      1      1     11     19      0      0      6   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      2      0      1      0      2      4      0      0      0   
17     z35   2980     99   1431   4951   1507  10607     42    103   3523   
18     z37      3      0      2      0      6      3      0      0      2   
19     z39     17      0     17      1      5     20      0      1      3   
20     z41     13      0      7      3      5      8      0      0      1   
21     z43     53      5     51     32     39    130      3      0     55   
22     z45     43      1     16     18     39     76      0      3     28   
23     z47     11      0      7      4     11     25      0      1      8   
24     z49   8020      6   2303    894    419    750      2    113    246   
25     z51     59      1     12      4     21     23      0      2      9   
26     z53     41      0     16      8     16     38      0      0     18   
27     z55      0      0      1      1      3      1      0      0      0   
28     z57    153      0     57     47   1912    982      0      1    326   

    CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  \
0       0      1      2      1      0      0      3      1      4      1   
1       0     10    131     64      0      2     21      0     29     10   
2       7     25    180    102      0     16     71      2    110     75   
3       0      8      7      6      0      6     10      1     16     22   
4       0      0      0      0      0      0      0      0      0      0   
5       0     70   5311   3549     11     26    424      8    603    252   
6       1      4     15      2      0      1      8      1      7     16   
7       0      8      4      0      0      0      7      0      9     15   
8       0      1      0      1      0      0      2      0      0      2   
9       0      1      0      4      0      1      7      2     10      3   
10      0      2      4      1      0      0      6      0     13     12   
11      0      1      4      3      0      1      5      0     11     29   
12      0      3      2      0      0      0      5      0      0      1   
13      0      4      5      0      0      0      8      0     12     26   
14      0      1     38     35      0      7      4      0     16      2   
15      0      0      1      0      0      0      0      0      1      1   
16      0      0      1      1      0      0      2      0      2      1   
17     56   1313   3635   2472    317    187  13782    100  16432   6607   
18      0      1      2      2      0      0      4      0      4      4   
19      1      8     11      5      1      1     14      3     19     30   
20      0      8      2      8      0      0      7      0     13     21   
21     42     35    

zCOFIPS         AFK_h      ALA_h         ALP_h         BDL_h         BGM_h  \
0      z01  2.442601e-02   0.000000  0.000000e+00  3.086364e-02  3.055296e-02   
1      z03  2.118008e-01   0.000000  6.762391e-02  6.174752e-02  3.980374e+01   
2      z05  6.273106e-01   0.000000  7.213805e-01  3.395972e-01  7.470362e+00   
3      z07  1.140698e-01   0.617773  2.254464e-01  3.087356e-02  1.325003e-01   
4      z09  0.000000e+00   0.000000  2.248632e-02  0.000000e+00  0.000000e+00   
5      z11  1.914420e+00   2.470728  2.141491e+00  2.361889e+00  8.061086e+00   
6      z13  1.059009e-01   0.000000  2.028523e-01  1.543572e-02  4.076631e-02   
7      z15  2.444383e-02   0.000000  9.018013e-02  3.087976e-02  3.057955e-02   
8      z17  2.443284e-02   0.000000  2.255206e-02  4.286247e-06  1.114310e-05   
9      z19  2.443420e-02   0.000000  9.015280e-02  6.780167e-12  3.056532e-02   
10     z21  1.872448e-01   0.000000  3.829404e-01  4.628139e-02  2.036832e-01   
11     z23  2.323507e-01   0.000000  2.102278e-01  1.080611e-01  3.095194e-02   
12     z25  3.258317e-02   0.000000  4.505184e-02  0.000000e+00  1.035736e-07   
13     z27  5.701335e-02   0.000000  4.507330e-02  1.944855e-07  4.074556e-02   
14     z29  8.152549e-03   0.000049  2.254681e-02  1.544836e-02  1.426873e-01   
15     z31  7.111662e-09   0.000000  4.796776e-07  8.631345e-10  7.892792e-08   
16     z33  1.628937e-02   0.000000  2.253684e-02  0.000000e+00  2.038330e-02   
17     z35  2.557495e+01  83.111450  3.543444e+01  7.924371e+01  1.685591e+01   
18     z37  2.443307e-02   0.000000  4.509185e-02  2.227261e-06  6.112636e-02   
19     z39  1.385013e-01   0.000000  3.832492e-01  1.544031e-02  5.095772e-02   
20     z41  1.059026e-01   0.000000  1.577881e-01  4.630975e-02  5.095296e-02   
21     z43  5.052084e-01   3.706052  1.262273e+00  5.248837e-01  4.586643e-01   
22     z45  4.317013e-01   0.617593  4.733196e-01  3.858750e-01  4.788536e-01   
23     z47  8.960259e-02   0.000000  1.578194e-01  6.174852e-02  1.120758e-01   
24     z49  6.691256e+01   7.689969  5.486501e+01  1.528000e+01  5.054765e+00   
25     z51  6.031527e-01   0.618119  3.836799e-01  1.236121e-01  3.158868e-01   
26     z53  6.103220e-01   0.616962  7.880934e-01  3.238155e-01  3.766529e-01   
27     z55  3.417635e-06   0.000000  2.253588e-02  1.543198e-02  3.057212e-02   
28     z57  1.466323e+00   0.617671  1.780792e+00  1.003385e+00  2.017730e+01   

           BNT_h      BRT_h         CDF_h         CEN_h         CHA_h  \
0   1.518742e-02   0.000000  0.000000e+00  1.311935e-08  0.000000e+00   
1   2.785160e-01   0.000000  0.000000e+00  2.329045e-01  0.000000e+00   
2   1.149631e+00   1.409413  6.215420e-01  1.219511e+00  2.779658e+00   
3   4.051815e-02   0.000000  0.000000e+00  5.481533e-02  0.000000e+00   
4   1.473746e-07   0.000000  0.000000e+00  0.000000e+00  0.000000e+00   
5   3.194899e+01   2.818585  9.324044e-01  3.606267e+01  0.000000e+00   
6   5.569637e-02   0.000000  0.000000e+00  9.588375e-02  3.972114e-01   
7   4.052174e-02   0.000000  0.000000e+00  4.111155e-02  0.000000e+00   
8   5.062943e-03   0.000000  0.000000e+00  4.109572e-02  0.000000e+00   
9   3.543988e-02   0.000000  0.000000e+00  1.369866e-02  0.000000e+00   
10  4.554890e-02   0.000000  1.094856e-07  9.584804e-02  1.770301e-05   
11  2.633855e-02   0.000000  1.242972e+00  2.808252e-02  0.000000e+00   
12  1.518836e-02   0.000000  0.000000e+00  1.370592e-02  0.000000e+00   
13  2.025237e-02   0.000000  3.106673e-01  4.109678e-02  0.000000e+00   
14  1.121039e-01   0.000000  0.000000e+00  1.098207e-01  1.260156e-04   
15  2.344292e-07   0.000000  0.000000e+00  4.760884e-07  0.000000e+00   
16  2.025506e-02   0.000000  0.000000e+00  8.313797e-07  8.709891e-07   
17  5.467939e+01  88.787729  4.554365e+01  5.024827e+01  3.136972e+01   
18  1.518957e-02   0.000000  0.000000e+00  2.739201e-02  0.000000e+00   
19  1.012922e-01   0.000000  3.108180e-01  4.110991e-02  3.971100e-01   
20  4.051289e-02   0.000000  0.000000e+

In [168]:
df_CountySum_wOutWF            = df_CountySum           .groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_wOutWF_Percent_SA = df_CountySum_Percent_SA.groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum_wOutWF            = df_CountySum_wOutWF.reset_index()
df_CountySum_wOutWF_Percent_SA = df_CountySum_wOutWF_Percent_SA.reset_index()

display(df_CountySum_wOutWF)
display(df_CountySum_wOutWF_Percent_SA)

WFCounty  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0           Davis County    192      2     70    117    721   6210      0   
1  Outside Wasatch Front    420      8    213    109   4826    670      4   
2       Salt Lake County   2980     99   1431   4951   1507  10607     42   
3            Utah County   8020      6   2303    894    419    750      2   
4           Weber County    153      0     57     47   1912    982      0   

   CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0      2   2551      0     70   5311   3549     11     26    424      8   
1     13    253    108    160    565    336      7    353    645    280   
2    103   3523     56   1313   3635   2472    317    187  13782    100   
3    113    246     28   2453    410    292     26     34    895     48   
4      1    326      1     58   2803   2900      0     33    208      7   

   DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0    603    252     22     12   3447      4      0    375    805      9   
1    742    568     69     41    286    244      3    172     60     60   
2  16432   6607    254    535   4342     85     23    453    830    148   
3   3343   6382    991     25    253     22     18     64     56    423   
4    297    149      8      9    458      6      0   1716    160      5   

   GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0      6    229    391      7    230    408    127     18    485    810   
1     42   1678    192    178   4735    385    344    173    639    167   
2     77   2322    448     41   1621  13609   2922     57  11755    641   
3    248    422     61     21    839   1786   3793     15    692     84   
4      6    131   1683      5    195    156     81     19    201   1679   

   HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0     19      0      0   5242     11    624  12982    482     79     61   
1     16     52     21    441    536    566   1219   1180    156    163   
2     40     21      7   5115    175  15875   9873  11553    963    796   
3      8      4      4    478     53    877   1120  14654   3437   3185   
4    131      1      0    940     21    235   5887    349     66     51   

   MID_h  MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  \
0    343   1003    497    241     94    744     39   1047   2047   7005   
1    441   1384    448    569     42    796   1076    617    267   2469   
2  14316  24957  12185    381    111  21337    543   1503   4923   7238   
3    933   1358    673     75     19   1290    304    214    262   1292   
4    195    390    149    364    519    292     59   5303    358  20982   

   OKL_h  ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  \
0      9    753    167    278    362     82    185    699    526   4721   
1    322   1592    586    513    179   2507   1096   1734    305    901   
2     96   9022   1955   3490    428    794    411   6670    651   3592   
3     35  31722   6424  10875     63    139     86  29315    100    576   
4     11    608    124    212   1757     80    602    552   2214   8400   

   RVD_h  RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  \
0    846    659   1273     80    193    335    869   4443     61   1492   
1    211    634   1653    645    471    913    824   3641    205    344   
2    763  18797  39546   1125   6059   3935  26298  74709    822   1544   
3    108   2571   3745   3307   6361  13749   3189   3847   2661    231   
4   1985    292    688     59    116    246    352   1293     34   3866   

   SPV_h  SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  \
0    270    452    864   1018   5077    943    800     96      1    887   
1    794    483     86     99    399    922   5202     20      1    213   
2   3373   9544    579    768   3375  26189   8359    117     12    786   
3  11343    507     73     61    359   1436   1410     14     55    124   
4    240    152    72

WFCounty      AFK_h      ALA_h      ALP_h      BDL_h  \
0           Davis County   1.914420   2.470728   2.141491   2.361889   
1  Outside Wasatch Front   4.199280   6.176547   5.844903   2.176312   
2       Salt Lake County  25.574954  83.111450  35.434437  79.243711   
3            Utah County  66.912558   7.689969  54.865006  15.279995   
4           Weber County   1.466323   0.617671   1.780792   1.003385   

       BGM_h      BNT_h      BRT_h      CDF_h      CEN_h      CHA_h  \
0   8.061086  31.948995   2.818585   0.932404  36.062671   0.000000   
1  49.913270   3.819788   5.638048   5.281967   4.261585  49.639484   
2  16.855913  54.679393  88.787729  45.543649  50.248273  31.369715   
3   5.054765   4.329971   2.822868  47.685879   4.381645  17.473542   
4  20.177303   5.286928   0.000000   0.621506   5.110619   1.588244   

       CHL_h      CLF_h      CLI_h      CMT_h      COA_h      CWH_h  \
0   2.263872  40.992549  36.524712   3.248777   5.932677   2.966092   
1   4.824996   4.765554   3.923303   2.165867  50.102623   4.395270   
2  32.549887  28.721960  26.102309  83.603343  30.468108  85.130653   
3  58.662485   3.723469   3.623595  10.180757   7.501831   6.029794   
4   1.765785  21.860076  29.889618   0.866291   6.064401   1.543785   

       DAN_h      DRA_h      EAG_h      ELK_h      EMT_h      FAR_h  \
0   3.685604   3.030824   2.078579   2.189233   2.851563  38.507816   
1  55.842064   3.899029   4.565573   5.843996   6.924734   3.602578   
2  23.772481  75.685391  46.958719  20.752088  82.574009  48.849586   
3  14.375911  15.923483  45.247498  70.189247   5.407783   3.528152   
4   2.395598   1.526727   1.215381   1.094648   2.307994   5.576777   

       FCS_h      FFD_h      FRR_h      FTH_h      GLA_h      GOS_h  \
0   2.936523   0.000000  14.064692  40.589050   1.740224   2.687590   
1  60.315859   5.066647   6.653221   3.786299  10.079356  10.843444   
2  25.298667  46.865554  17.203950  42.239728  24.115084  21.501639   
3   8.585140  45.601132   3.119141   4.122367  62.516640  62.554264   
4   2.936275   2.533239  59.022030   9.327010   1.615891   2.480895   

       GRL_h      HAR_h      HDT_h      HEB_h      HER_h      HGH_h  \
0   5.263368  14.834367   4.144664   3.493816   2.770296   2.224159   
1  34.081465   7.366413  60.102858  60.101780   2.761203   5.499745   
2  48.037420  17.069217  21.611883  21.935391  81.987988  39.824951   
3   9.545557   2.884667  11.251565  11.632838  11.394416  51.120962   
4   3.130625  57.908329   2.960430   2.907420   1.150802   1.396504   

       HNF_h      HOL_h      HOO_h      HVL_h      IND_h      INT_h  \
0   8.385174   3.818837  24.149742  12.238416   1.681761   2.001325   
1  53.669665   4.947788   5.463510   6.498654  55.503759  58.043846   
2  22.640486  84.096280  19.340314  19.324144  27.749560  20.013265   
3   7.547274   5.546261   3.306474   4.774825  13.455204  16.011308   
4   7.826160   1.656713  47.802997  57.228889   1.681778   4.002529   

       KAY_h      KMS_h      KMT_h      LAY_h      LEH_h      LIN_h  \
0  42.136901   2.435391   3.689780  41.360396   1.892232   2.035643   
1   4.036440  60.736065   3.513714   4.156914   4.526713   4.230831   
2  41.554363  23.719296  86.093687  31.815180  40.803805  21.236614   
3   4.453883  10.003705   5.307062   3.865882  51.478192  70.845420   
4   7.883031   3.176611   1.459853  18.865566   1.365485   1.719427   

       MAP_h      MID_h      MLC_h      MMT_h      MRG_h      MSL_h  \
0   1.830443   2.372628   3.623681   3.809057  15.939706  13.507795   
1   4.632572   3.170139   4.965977   3.691947  32.311029   5.943218   
2  19.915070  86.873518  84.997891  85.971777  24.103416  16.067447   
3  72.187400   6.280251   5.013825   5.363219   5.451996   3.059840   
4   1.503524   1.368580   1.464296   1.228049  22.260060  61.484715   

       MUR_h      MWY_h      NOG_h      NSL_h      OGD_h      OKL_h  \
0   3.255798   2.756830  12.472688  25.860197  17.965122   2.651902   
1   3.595126  49.591443  

In [169]:
# bu map unit
# block group
df_CountySum_wOutWF_Percent_MU = df_CountySum_wOutWF.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    df_CountySum_wOutWF_Percent_MU[x] = df_CountySum_wOutWF_Percent_MU[x] / df_CountySum_wOutWF_Percent_MU['TTL_h'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    df_CountySum_wOutWF_Percent_MU[y] = df_CountySum_wOutWF_Percent_MU[y] / df_CountySum_wOutWF_Percent_MU['TTL_w'] * 100

df_CountySum_wOutWF_Percent_MU

WFCounty     AFK_h     ALA_h     ALP_h     BDL_h     BGM_h  \
0           Davis County  0.171675  0.001788  0.062590  0.104615  0.644677   
1  Outside Wasatch Front  0.156034  0.002972  0.079132  0.040495  1.792906   
2       Salt Lake County  0.447420  0.014864  0.214852  0.743348  0.226262   
3            Utah County  3.389358  0.002536  0.973278  0.377816  0.177075   
4           Weber County  0.144166  0.000000  0.053709  0.044286  1.801598   

      BNT_h     BRT_h     CDF_h     CEN_h     CHA_h     CHL_h     CLF_h  \
0  5.552625  0.000000  0.001788  2.280957  0.000000  0.062590  4.748791   
1  0.248911  0.001486  0.004830  0.093992  0.040123  0.059442  0.209903   
2  1.592545  0.006306  0.015465  0.528946  0.008408  0.197135  0.545762   
3  0.316960  0.000845  0.047755  0.103963  0.011833  1.036670  0.173271   
4  0.925298  0.000000  0.000942  0.307176  0.000942  0.054651  2.641150   

      CLI_h     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h  \
0  3.173312  0.009836  0.023248  0.379116  0.007153  0.539168  0.225324   
1  0.124827  0.002601  0.131143  0.239624  0.104023  0.275660  0.211017   
2  0.371148  0.047595  0.028076  2.069242  0.015014  2.467115  0.991981   
3  0.123403  0.010988  0.014369  0.378239  0.020285  1.412796  2.697117   
4  2.732549  0.000000  0.031095  0.195990  0.006596  0.279851  0.140397   

      ELK_h     EMT_h     FAR_h     FCS_h     FFD_h     FRR_h     FTH_h  \
0  0.019671  0.010730  3.082109  0.003577  0.000000  0.335303  0.719785   
1  0.025634  0.015232  0.106252  0.090648  0.001115  0.063900  0.022291   
2  0.038136  0.080325  0.651912  0.012762  0.003453  0.068014  0.124617   
3  0.418810  0.010565  0.106921  0.009297  0.007607  0.027047  0.023666   
4  0.007538  0.008480  0.431554  0.005654  0.000000  1.616915  0.150761   

      GLA_h     GOS_h     GRL_h     HAR_h     HDT_h     HEB_h     HER_h  \
0  0.008047  0.005365  0.204759  0.349610  0.006259  0.205653  0.364810   
1  0.022291  0.015603  0.623393  0.071330  0.066129  1.759098  0.143031   
2  0.022221  0.011561  0.348627  0.067263  0.006156  0.243378  2.043268   
3  0.178765  0.104808  0.178343  0.025779  0.008875  0.354572  0.754787   
4  0.004711  0.005654  0.123436  1.585821  0.004711  0.183740  0.146992   

      HGH_h     HNF_h     HOL_h     HOO_h     HVL_h     IND_h     INT_h  \
0  0.113556  0.016095  0.433659  0.724255  0.016989  0.000000  0.000000   
1  0.127799  0.064271  0.237395  0.062042  0.005944  0.019319  0.007802   
2  0.438712  0.008558  1.764906  0.096240  0.006006  0.003153  0.001051   
3  1.602972  0.006339  0.292448  0.035500  0.003381  0.001690  0.001690   
4  0.076323  0.017903  0.189394  1.582052  0.123436  0.000942  0.000000   

      KAY_h     KMS_h     KMT_h      LAY_h     LEH_h     LIN_h     MAP_h  \
0  4.687095  0.009836  0.557945  11.607758  0.430977  0.070637  0.054543   
1  0.163836  0.199129  0.210274   0.452870  0.438381  0.057956  0.060556   
2  0.767971  0.026275  2.383487   1.482341  1.734578  0.144586  0.119512   
3  0.202009  0.022398  0.370632   0.473327  6.192974  1.452522  1.346023   
4  0.885723  0.019787  0.221431   5.547075  0.328848  0.062189  0.048055   

      MID_h     MLC_h     MMT_h     MRG_h     MSL_h     MUR_h     MWY_h  \
0  0.306691  0.896825  0.444389  0.215488  0.084049  0.665242  0.034872   
1  0.163836  0.514169  0.166436  0.211389  0.015603  0.295722  0.399744   
2  2.149417  3.747067  1.829467  0.057204  0.016666  3.203557  0.081527   
3  0.394298  0.573909  0.284419  0.031696  0.008030  0.545171  0.128474   
4  0.183740  0.367481  0.140397  0.342982  0.489032  0.275139  0.055593   

      NOG_h     NSL_h      OGD_h     OKL_h      ORM_h     PAY_h     PGR_h  \
0  0.936167  1.830310   6.263468  0.008047   0.673289  0.149322  0.248572   
1  0.229221  0.099193   0.917257  0.119626   0.591443  0.217705  0.190584   
2  0.225662  0.739144   1.086720  0.014414   1.354571  0.293525  0.523992   
3  0.090439  0.110725   0.546016  0.014791  13.406135  2.714867  4.595918   

In [170]:
df_CountySum_wOutWF           .to_json(os.path.join(dirResults, "countydata_number.json"    ),orient='records')
df_CountySum_wOutWF_Percent_SA.to_json(os.path.join(dirResults, "countydata_percent_sa.json"),orient='records')
df_CountySum_wOutWF_Percent_MU.to_json(os.path.join(dirResults, "countydata_percent_mu.json"),orient='records')